In [105]:
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from pytorch_tabnet.tab_model import TabNetClassifier
#from pytorch_tabnet.tab_model import TabNetModel
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
import optuna
import torch
from sklearn import svm
import tensorflow as tf
from tensorflow import feature_column
from tensorflow.keras import layers
from tqdm.auto import tqdm
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer
from sklearn.decomposition import PCA

In [106]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

In [107]:
train_data = pd.read_csv("./train.csv")

In [108]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

train_data = train_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR'], axis = 1)

In [109]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

train_data.drop(colls, inplace = True, axis = 1)

82


In [110]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  \
0          1   0.533433  T050304            1   NaN   NaN  NaN   NaN   NaN   
1          2   0.541819  T050307            1   NaN   NaN  NaN   NaN   NaN   
2          1   0.531267  T050304            1   NaN   NaN  NaN   NaN   NaN   
3          2   0.537325  T050307            1   NaN   NaN  NaN   NaN   NaN   
4          1   0.531590  T050304            1   NaN   NaN  NaN   NaN   NaN   
..       ...        ...      ...          ...   ...   ...  ...   ...   ...   
593        1   0.526546  T100306            2   2.0  95.0  0.0  45.0  10.0   
594        0   0.524022  T050304            1   NaN   NaN  NaN   NaN   NaN   
595        0   0.521289  T050304            1   NaN   NaN  NaN   NaN   NaN   
596        1   0.531375  T100304            3  40.0  94.0  0.0  45.0  11.0   
597        1   0.533702  T100306            3  21.0  87.0  0.0  45.0  10.0   

     X_6   X_7   X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16  \
0    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
1    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
2    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
3    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
4    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
..   ...   ...   ...   ...   ...    ...    ...    ...   ...   ...    ...   
593  0.0  50.0  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5   
594  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
595  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
596  0.0  45.0  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5   
597  0.0  61.0  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5   

      X_17   X_18   X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27  \
0      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...   ...   ...   ...    ...    ...   
593  248.0  247.3  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
596  248.1  247.3  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0   
597  248.0  247.3  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0   

      X_28   X_29   X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
597  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   

      X_38  X_39  X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  \
0      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN   NaN 

In [111]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [112]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == len(T050304) :
        T050304_col.append(col)
print(len(T050304_col))

T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == len(T050307) :
        T050307_col.append(col)
print(len(T050307_col))

T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == len(T010305) :
        T010305_col.append(col)
print(len(T010305_col))

T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == len(T010306) :
        T010306_col.append(col)
print(len(T010306_col))

T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == len(T100304) :
        T100304_col.append(col)
print(len(T100304_col))

T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == len(T100306) :
        T100306_col.append(col)
print(len(T100306_col))

825
818
1907
1907
2122
2122


In [113]:
T050304.drop(T050304_col, inplace = True, axis = 1)
T050307.drop(T050307_col, inplace = True, axis = 1)
T010305.drop(T010305_col, inplace = True, axis = 1)
T010306.drop(T010306_col, inplace = True, axis = 1)
T100304.drop(T100304_col, inplace = True, axis = 1)
T100306.drop(T100306_col, inplace = True, axis = 1)

In [114]:
T051 = list(set(T050307_col)-set(T050304_col))
T052 = list(set(T050304_col)-set(T050307_col))
T5drop = T051 + T052

T011 = list(set(T010305_col)-set(T010306_col))
T012 = list(set(T010306_col)-set(T010305_col))
T0drop = T011 + T012

T101 = list(set(T100304_col)-set(T100306_col))
T102 = list(set(T100306_col)-set(T100304_col))
T1drop = T101 + T102

In [115]:
T05 = pd.concat([T050304, T050307])
T01 = pd.concat([T010305, T010306])
T10 = pd.concat([T100304, T100306])

T05.drop(T5drop, inplace = True, axis = 1)
T01.drop(T0drop, inplace = True, axis = 1)
T10.drop(T1drop, inplace = True, axis = 1)

#T05 = T05.fillna(T05.mean())
#T01 = T01.fillna(T01.mean())
#T10 = T10.fillna(T10.mean())

T05 = T05.fillna(0)
T01 = T01.fillna(0)
T10 = T10.fillna(0)

In [116]:
T05_cols = []
for col in T05 :
    if 'X' in col and T05[col].std() == 0 :
        T05_cols.append(col)
print(len(T05_cols))

T01_cols = []
for col in T01 :
    if 'X' in col and T01[col].std() == 0 :
        T01_cols.append(col)
print(len(T01_cols))

T10_cols = []
for col in T10 :
    if 'X' in col and T10[col].std() == 0 :
        T10_cols.append(col)
print(len(T10_cols))

184
144
91


In [117]:
T05.drop(T05_cols, inplace = True, axis = 1)
T01.drop(T01_cols, inplace = True, axis = 1)
T10.drop(T10_cols, inplace = True, axis = 1)

# T05

In [118]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [119]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)

T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
index                                                                           
0               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
2               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
4               0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
6               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
8               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
...             ...    ...    ...    ...    ...       ...       ...       ...   
549             0.0   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292   
550             0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
551             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
552             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
555             0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   

          X_139     X_140     X_141  X_143  X_144  X_145     X_146     X_148  \
index                                                                          
0     -0.024793 -0.052154  0.023438    0.0   -1.0    0.0 -0.003454  0.000000   
2      0.024793 -0.029478  0.315104    0.0    0.0    0.0  0.563040 -0.074074   
4     -0.008264 -0.043084 -0.049479    0.0   -1.0    0.0 -0.348877  0.000000   
6      0.002755 -0.043084 -1.195312    0.0   -2.0    0.0 -4.113990  0.000000   
8     -0.002755 -0.047619  0.263021    0.0    0.0    0.0  0.514680  0.000000   
...         ...       ...       ...    ...    ...    ...       ...       ...   
549   -1.049587 -0.882086 -0.898437    0.0    0.0    0.0  0.373057  1.037037   
550   -1.049587 -0.891156 -0.929687    0.0   -1.0    0.0  0.158895  1.037037   
551   -1.044077 -0.886621 -0.695312    0.0    0.0    0.0  0.618307  1.037037   
552   -1.033058 -0.877551 -0.919271    0.0    0.0    0.0  0.158895  1.037037   
555   -1.082645 -0.877551 -1.263021    0.0   -1.0    0.0 -0.873921  1.111111   

          X_149   X_150  X_151  X_152  X_153  X_155  X_156  X_157  X_159  \
index                                                                      
0      0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0    0.0   -1.0   
2      0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0    0.0    0.0   
4      0.000000  0.0625    0.0    0.0   -1.0    0.0    0.1    0.1   -1.0   
6      0.000000  0.0000    0.0    0.1    0.0   -1.0    0.0    0.0    0.0   
8      0.000000  0.0625    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...         ...     ...    ...    ...    ...    ...    ...    ...    ...   
549    1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0    0.0   -1.0   
550    1.163636  0.8750    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
551    1.163636  0.8750   -1.0    0.0   -1.0   -1.0    0.0    0.0   -1.0   
552    1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0   -0.1   -1.0   
555    1.236364  0.8750    0.0    0.0    0.0   -1.0    0.0    0.0    0.0   

       X_160  X_161  X_163  X_164  X_165  X_167  X_168  X_169  X_171  X_172  \
index                                                                         
0        0.0    0.0   -0.1    0.0   -0.5   -1.0    0.0    0.0    0.0    0.0   
2        0.0    0.0   -0.1    0.0   -0.5   -1.0    0.0    0.0   -1.0    0.0   
4        0.0    0.0    0.0    1.0    0.5   -1.0    0.0    0.0   -1.0    0.0   
6        0.0    0.0    0.0    0.0   -0.5    0.0    0.0    0.0   -1.0    0.0   
8        0.0    0.0    0.0    1.0    0.5    0.0    0.0    0.0    0.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.0    0.0   -0.1    0.0   -0.5    0.0    0.0    0.0    0.0    0.0   
550      0.0    0.0    0.0    1.0    0.5    0.0    0.0    0.0   -1.0    0.0   
551      0.0    0.0    0.0    0.0    0.5    0.0    0.1    0.0    0.0    0.0   
552      0.1    0.0   -0.1    0.0   -0.5    0.0    0.0

In [120]:
#13
setup_rgs = setup(data = T05_data, target = T05_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [121]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [122]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [123]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408   
85            0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
86            0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
87            0.0    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157   
88            0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
89            0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
90            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
91            0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
92            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
93            0.0    0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709   
94            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
95            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
96            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
97            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
98            0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
99            0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
100           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
101           0.0   -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826   
102           0.0    0.0    0.0   -1.0    0.0  0.573022  0.570994  0.573612   
103           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
104           0.0    0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386   
105           0.0    0.0    0.0    0.0    0.0 -0.420893 -0.418864 -0.420785   
106           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
107           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
108           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
109           0.0    0.0    0.0    0.0    0.0  0.796146  0.794118  0.799796   
110           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
111           0.0    0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491   
112           0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
113           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
114           0.0    0.0    0.0    0.0    0.0  1.023327  1.021298  1.025981   
115           0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
117           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
118           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   
119           0.0    0.0    0.0    0.0    0.0  0.767748  0.765720  0.769231   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
84   0.702479  0.637188  ...     0.0  0.318899  0.561440  0.165000  0.055581   
85  -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
86  -0.112948 -0.083900  ...     0.0  0.133931  0.010957  0.694286  0.066426   
87   1.325069  1.190476  ...     1.0  0.203835  0.453953 -0.517857  0.077723   
88  -0.663912 -0.632653  ...     1.0  0.263842 -0.222280 -0.676429  0.091731   
89   0.741047  0.691610  ...     0.0 -0.118466  0.130446  0.222143  0.048351   
90  -0.008264 -0.052154  ...     0.0 -1.266625 -1.042525  0.355000 -1.000904   
91  -0.162534 -0.147392  ...     0.0 -3.253634 -2.855205 -3.568571 -2.499322   
92   0.338843  0.342404  ...     1.0 -1.125580 -0.983042  0.028571 -0.761862   
93  -0.713499 -0.664399  ...     0.0 -0.266935 -0.181059  0.390714  0.074108   
94  -0.228650 -0.229025  ...     1.0 -0.165481 -0.003131  0.042857 -0.301853   
95   0.355372  0.356009  ...     1.0 -0.918961 -0.811375  0.157857 -1.117488   
96   0.636364  0.596372  ...     1.0  0.2

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408   
85            0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
86            0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
87            0.0    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157   
88            0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
89            0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
90            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
91            0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
92            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
93            0.0    0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709   
94            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
95            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
96            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
97            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
98            0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
99            0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
100           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
101           0.0   -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826   
102           0.0    0.0    0.0   -1.0    0.0  0.573022  0.570994  0.573612   
103           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
104           0.0    0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386   
105           0.0    0.0    0.0    0.0    0.0 -0.420893 -0.418864 -0.420785   
106           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
107           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
108           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
109           0.0    0.0    0.0    0.0    0.0  0.796146  0.794118  0.799796   
110           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
111           0.0    0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491   
112           0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
113           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
114           0.0    0.0    0.0    0.0    0.0  1.023327  1.021298  1.025981   
115           0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
117           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
118           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   
119           0.0    0.0    0.0    0.0    0.0  0.767748  0.765720  0.769231   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
84   0.702479  0.637188  ...     0.0  0.318899  0.561440  0.165000  0.055581   
85  -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
86  -0.112948 -0.083900  ...     0.0  0.133931  0.010957  0.694286  0.066426   
87   1.325069  1.190476  ...     1.0  0.203835  0.453953 -0.517857  0.077723   
88  -0.663912 -0.632653  ...     1.0  0.263842 -0.222280 -0.676429  0.091731   
89   0.741047  0.691610  ...     0.0 -0.118466  0.130446  0.222143  0.048351   
90  -0.008264 -0.052154  ...     0.0 -1.266625 -1.042525  0.355000 -1.000904   
91  -0.162534 -0.147392  ...     0.0 -3.253634 -2.855205 -3.568571 -2.499322   
92   0.338843  0.342404  ...     1.0 -1.125580 -0.983042  0.028571 -0.761862   
93  -0.713499 -0.664399  ...     0.0 -0.266935 -0.181059  0.390714  0.074108   
94  -0.228650 -0.229025  ...     1.0 -0.165481 -0.003131  0.042857 -0.301853   
95   0.355372  0.356009  ...     1.0 -0.918961 -0.811375  0.157857 -1.117488   
96   0.636364  0.596372  ...     1.0  0.2

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408   
85            0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
86            0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
87            0.0    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157   
88            0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
89            0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
90            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
91            0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
92            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
93            0.0    0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709   
94            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
95            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
96            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
97            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
98            0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
99            0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
100           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
101           0.0   -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826   
102           0.0    0.0    0.0   -1.0    0.0  0.573022  0.570994  0.573612   
103           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
104           0.0    0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386   
105           0.0    0.0    0.0    0.0    0.0 -0.420893 -0.418864 -0.420785   
106           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
107           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
108           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
109           0.0    0.0    0.0    0.0    0.0  0.796146  0.794118  0.799796   
110           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
111           0.0    0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491   
112           0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
113           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
114           0.0    0.0    0.0    0.0    0.0  1.023327  1.021298  1.025981   
115           0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
117           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
118           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   
119           0.0    0.0    0.0    0.0    0.0  0.767748  0.765720  0.769231   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
84   0.702479  0.637188  ...     0.0  0.318899  0.561440  0.165000  0.055581   
85  -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
86  -0.112948 -0.083900  ...     0.0  0.133931  0.010957  0.694286  0.066426   
87   1.325069  1.190476  ...     1.0  0.203835  0.453953 -0.517857  0.077723   
88  -0.663912 -0.632653  ...     1.0  0.263842 -0.222280 -0.676429  0.091731   
89   0.741047  0.691610  ...     0.0 -0.118466  0.130446  0.222143  0.048351   
90  -0.008264 -0.052154  ...     0.0 -1.266625 -1.042525  0.355000 -1.000904   
91  -0.162534 -0.147392  ...     0.0 -3.253634 -2.855205 -3.568571 -2.499322   
92   0.338843  0.342404  ...     1.0 -1.125580 -0.983042  0.028571 -0.761862   
93  -0.713499 -0.664399  ...     0.0 -0.266935 -0.181059  0.390714  0.074108   
94  -0.228650 -0.229025  ...     1.0 -0.165481 -0.003131  0.042857 -0.301853   
95   0.355372  0.356009  ...     1.0 -0.918961 -0.811375  0.157857 -1.117488   
96   0.636364  0.596372  ...     1.0  0.2

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408   
85            0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
86            0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
87            0.0    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157   
88            0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
89            0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
90            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
91            0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
92            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
93            0.0    0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709   
94            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
95            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
96            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
97            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
98            0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
99            0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
100           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
101           0.0   -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826   
102           0.0    0.0    0.0   -1.0    0.0  0.573022  0.570994  0.573612   
103           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
104           0.0    0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386   
105           0.0    0.0    0.0    0.0    0.0 -0.420893 -0.418864 -0.420785   
106           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
107           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
108           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
109           0.0    0.0    0.0    0.0    0.0  0.796146  0.794118  0.799796   
110           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
111           0.0    0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491   
112           0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
113           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
114           0.0    0.0    0.0    0.0    0.0  1.023327  1.021298  1.025981   
115           0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
117           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
118           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   
119           0.0    0.0    0.0    0.0    0.0  0.767748  0.765720  0.769231   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
84   0.702479  0.637188  ...     0.0  0.318899  0.561440  0.165000  0.055581   
85  -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
86  -0.112948 -0.083900  ...     0.0  0.133931  0.010957  0.694286  0.066426   
87   1.325069  1.190476  ...     1.0  0.203835  0.453953 -0.517857  0.077723   
88  -0.663912 -0.632653  ...     1.0  0.263842 -0.222280 -0.676429  0.091731   
89   0.741047  0.691610  ...     0.0 -0.118466  0.130446  0.222143  0.048351   
90  -0.008264 -0.052154  ...     0.0 -1.266625 -1.042525  0.355000 -1.000904   
91  -0.162534 -0.147392  ...     0.0 -3.253634 -2.855205 -3.568571 -2.499322   
92   0.338843  0.342404  ...     1.0 -1.125580 -0.983042  0.028571 -0.761862   
93  -0.713499 -0.664399  ...     0.0 -0.266935 -0.181059  0.390714  0.074108   
94  -0.228650 -0.229025  ...     1.0 -0.165481 -0.003131  0.042857 -0.301853   
95   0.355372  0.356009  ...     1.0 -0.918961 -0.811375  0.157857 -1.117488   
96   0.636364  0.596372  ...     1.0  0.2

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408   
85            0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
86            0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
87            0.0    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157   
88            0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
89            0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
90            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
91            0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
92            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
93            0.0    0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709   
94            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
95            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
96            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
97            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
98            0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
99            0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
100           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
101           0.0   -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826   
102           0.0    0.0    0.0   -1.0    0.0  0.573022  0.570994  0.573612   
103           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
104           0.0    0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386   
105           0.0    0.0    0.0    0.0    0.0 -0.420893 -0.418864 -0.420785   
106           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
107           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
108           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
109           0.0    0.0    0.0    0.0    0.0  0.796146  0.794118  0.799796   
110           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
111           0.0    0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491   
112           0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
113           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
114           0.0    0.0    0.0    0.0    0.0  1.023327  1.021298  1.025981   
115           0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
117           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
118           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   
119           0.0    0.0    0.0    0.0    0.0  0.767748  0.765720  0.769231   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
84   0.702479  0.637188  ...     0.0  0.318899  0.561440  0.165000  0.055581   
85  -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
86  -0.112948 -0.083900  ...     0.0  0.133931  0.010957  0.694286  0.066426   
87   1.325069  1.190476  ...     1.0  0.203835  0.453953 -0.517857  0.077723   
88  -0.663912 -0.632653  ...     1.0  0.263842 -0.222280 -0.676429  0.091731   
89   0.741047  0.691610  ...     0.0 -0.118466  0.130446  0.222143  0.048351   
90  -0.008264 -0.052154  ...     0.0 -1.266625 -1.042525  0.355000 -1.000904   
91  -0.162534 -0.147392  ...     0.0 -3.253634 -2.855205 -3.568571 -2.499322   
92   0.338843  0.342404  ...     1.0 -1.125580 -0.983042  0.028571 -0.761862   
93  -0.713499 -0.664399  ...     0.0 -0.266935 -0.181059  0.390714  0.074108   
94  -0.228650 -0.229025  ...     1.0 -0.165481 -0.003131  0.042857 -0.301853   
95   0.355372  0.356009  ...     1.0 -0.918961 -0.811375  0.157857 -1.117488   
96   0.636364  0.596372  ...     1.0  0.2

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408   
85            0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
86            0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
87            0.0    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157   
88            0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
89            0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
90            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
91            0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
92            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
93            0.0    0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709   
94            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
95            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
96            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
97            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
98            0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
99            0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
100           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
101           0.0   -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826   
102           0.0    0.0    0.0   -1.0    0.0  0.573022  0.570994  0.573612   
103           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
104           0.0    0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386   
105           0.0    0.0    0.0    0.0    0.0 -0.420893 -0.418864 -0.420785   
106           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
107           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
108           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
109           0.0    0.0    0.0    0.0    0.0  0.796146  0.794118  0.799796   
110           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
111           0.0    0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491   
112           0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
113           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
114           0.0    0.0    0.0    0.0    0.0  1.023327  1.021298  1.025981   
115           0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
117           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
118           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   
119           0.0    0.0    0.0    0.0    0.0  0.767748  0.765720  0.769231   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
84   0.702479  0.637188  ...     0.0  0.318899  0.561440  0.165000  0.055581   
85  -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
86  -0.112948 -0.083900  ...     0.0  0.133931  0.010957  0.694286  0.066426   
87   1.325069  1.190476  ...     1.0  0.203835  0.453953 -0.517857  0.077723   
88  -0.663912 -0.632653  ...     1.0  0.263842 -0.222280 -0.676429  0.091731   
89   0.741047  0.691610  ...     0.0 -0.118466  0.130446  0.222143  0.048351   
90  -0.008264 -0.052154  ...     0.0 -1.266625 -1.042525  0.355000 -1.000904   
91  -0.162534 -0.147392  ...     0.0 -3.253634 -2.855205 -3.568571 -2.499322   
92   0.338843  0.342404  ...     1.0 -1.125580 -0.983042  0.028571 -0.761862   
93  -0.713499 -0.664399  ...     0.0 -0.266935 -0.181059  0.390714  0.074108   
94  -0.228650 -0.229025  ...     1.0 -0.165481 -0.003131  0.042857 -0.301853   
95   0.355372  0.356009  ...     1.0 -0.918961 -0.811375  0.157857 -1.117488   
96   0.636364  0.596372  ...     1.0  0.2

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.406694  0.404665  0.400408   
85            0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
86            0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
87            0.0    0.0    0.0   -1.0    0.0  0.662272  0.660243  0.657157   
88            0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
89            0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
90            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
91            0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
92            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
93            0.0    0.0    0.0   -1.0    0.0 -0.412779 -0.414807 -0.416709   
94            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
95            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
96            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
97            0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
98            0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
99            0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
100           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
101           0.0   -1.0    0.0   -1.0    0.0  0.211968  0.209939  0.206826   
102           0.0    0.0    0.0   -1.0    0.0  0.573022  0.570994  0.573612   
103           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
104           0.0    0.0    0.0    0.0    0.0 -0.560852 -0.558824 -0.561386   
105           0.0    0.0    0.0    0.0    0.0 -0.420893 -0.418864 -0.420785   
106           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
107           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
108           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
109           0.0    0.0    0.0    0.0    0.0  0.796146  0.794118  0.799796   
110           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
111           0.0    0.0   -1.0    0.0    0.0  0.996957  0.994929  0.999491   
112           0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
113           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
114           0.0    0.0    0.0    0.0    0.0  1.023327  1.021298  1.025981   
115           0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
117           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
118           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   
119           0.0    0.0    0.0    0.0    0.0  0.767748  0.765720  0.769231   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
84   0.702479  0.637188  ...     0.0  0.318899  0.561440  0.165000  0.055581   
85  -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
86  -0.112948 -0.083900  ...     0.0  0.133931  0.010957  0.694286  0.066426   
87   1.325069  1.190476  ...     1.0  0.203835  0.453953 -0.517857  0.077723   
88  -0.663912 -0.632653  ...     1.0  0.263842 -0.222280 -0.676429  0.091731   
89   0.741047  0.691610  ...     0.0 -0.118466  0.130446  0.222143  0.048351   
90  -0.008264 -0.052154  ...     0.0 -1.266625 -1.042525  0.355000 -1.000904   
91  -0.162534 -0.147392  ...     0.0 -3.253634 -2.855205 -3.568571 -2.499322   
92   0.338843  0.342404  ...     1.0 -1.125580 -0.983042  0.028571 -0.761862   
93  -0.713499 -0.664399  ...     0.0 -0.266935 -0.181059  0.390714  0.074108   
94  -0.228650 -0.229025  ...     1.0 -0.165481 -0.003131  0.042857 -0.301853   
95   0.355372  0.356009  ...     1.0 -0.918961 -0.811375  0.157857 -1.117488   
96   0.636364  0.596372  ...     1.0  0.2

In [124]:
T05_final_regression_model = finalize_model(T05_model_et)

T05_prediction = predict_model(T05_final_regression_model, data=T05_data)
T05_prediction

T05_datas = T05_prediction['prediction_label']
T05_datas = pd.DataFrame(T05_datas.values, columns = ['Y_Quality'])

T05y_idx= T05_class.index
T05y_idx = pd.DataFrame(T05y_idx, columns = ['index'])
T05_datas = pd.concat([T05y_idx, T05_datas], axis = 1)
T05_datas = T05_datas.set_index('index')
T05_datas

Y_Quality
index           
0       0.533433
2       0.531267
4       0.531590
6       0.533665
8       0.531821
...          ...
549     0.533711
550     0.533695
551     0.525271
552     0.529806
555     0.521406

[120 rows x 1 columns]

In [125]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T05_datas, 
                   target=T05_class, 
                   fold=5,
                   session_id=4)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [126]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [127]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [128]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]

for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.538629        2                 2            0.3592
85    0.533695        1                 1            0.4590
86    0.520911        0                 0            0.4289
87    0.522368        0                 0            0.4289
88    0.537560        2                 2            0.3592
89    0.544129        2                 2            0.3592
90    0.533711        1                 1            0.4590
91    0.520252        0                 0            0.4289
92    0.529236        1                 1            0.4590
93    0.521259        0                 0            0.4289
94    0.544584        2                 2            0.3592
95    0.516711        0                 0            0.4289
96    0.528817        1                 1            0.4590
97    0.524567        0                 0            0.4289
98    0.533665        1                 1            0.4590
99    0.522300        0                 0            0.4289
100   0.540106        2                 2            0.3592
101   0.521544        0                 0            0.4289
102   0.524551        0                 0            0.4289
103   0.538508        2                 2            0.3592
104   0.531254        1                 1            0.4590
105   0.538049        2                 2            0.3592
106   0.528552        1                 1            0.4590
107   0.541819        2                 2            0.3592
108   0.529806        1                 1            0.4590
109   0.532170        1                 1            0.4590
110   0.555616        2                 2            0.3592
111   0.521524        0                 0            0.4289
112   0.518960        0                 0            0.4289
113   0.533632        1                 1            0.4590
114   0.521987        0                 0            0.4289
115   0.537833        2                 2            0.3592
116   0.526868        1                 1            0.4590
117   0.527887        1                 1            0.4590
118   0.526346        1                 1            0.4590
119   0.529035        1                 1            0.4590

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.538629        2                 2               1.0
85    0.533695        1                 1               1.0
86    0.520911        0                 0               1.0
87    0.522368        0                 0               1.0
88    0.537560        2                 2               1.0
89    0.544129        2                 2               1.0
90    0.533711        1                 1               1.0
91    0.520252        0                 0               1.0
92    0.529236        1                 1               1.0
93    0.521259        0                 0               1.0
94    0.544584        2                 2               1.0
95    0.516711        0                 0               1.0
96    0.528817        1                 1               1.0
97    0.524567        0                 0               1.0
98    0.533665        1                 1               1.0
99    0.522300        0                 0               1.0
100   0.540106        2                 2               1.0
101   0.521544        0                 0               1.0
102   0.524551        0                 0               1.0
103   0.538508        2                 2               1.0
104   0.531254        1                 1               1.0
105   0.538049        2                 2               1.0
106   0.528552        1                 1               1.0
107   0.541819        2                 2               1.0
108   0.529806        1                 1               1.0
109   0.532170        1                 1               1.0
110   0.555616        2                 2               1.0
111   0.521524        0                 0               1.0
112   0.518960        0                 0               1.0
113   0.533632        1                 1               1.0
114   0.521987        0                 0               1.0
115   0.537833        2                 2               1.0
116   0.526868        1                 1               1.0
117   0.527887        1                 1               1.0
118   0.526346        1                 1               1.0
119   0.529035        1                 1               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.538629        2                 2            0.4957
85    0.533695        1                 1            0.5771
86    0.520911        0                 0            0.5528
87    0.522368        0                 0            0.5528
88    0.537560        2                 2            0.4959
89    0.544129        2                 2            0.4957
90    0.533711        1                 1            0.5771
91    0.520252        0                 0            0.5528
92    0.529236        1                 1            0.5802
93    0.521259        0                 0            0.5528
94    0.544584        2                 2            0.4957
95    0.516711        0                 0            0.5528
96    0.528817        1                 1            0.5802
97    0.524567        0                 0            0.5569
98    0.533665        1                 1            0.5771
99    0.522300        0                 0            0.5528
100   0.540106        2                 2            0.4957
101   0.521544        0                 0            0.5528
102   0.524551        0                 0            0.5569
103   0.538508        2                 2            0.4957
104   0.531254        1                 1            0.5802
105   0.538049        2                 2            0.4959
106   0.528552        1                 1            0.5802
107   0.541819        2                 2            0.4957
108   0.529806        1                 1            0.5802
109   0.532170        1                 1            0.5803
110   0.555616        2                 2            0.4957
111   0.521524        0                 0            0.5528
112   0.518960        0                 0            0.5528
113   0.533632        1                 1            0.5771
114   0.521987        0                 0            0.5528
115   0.537833        2                 2            0.4959
116   0.526868        1                 1            0.5802
117   0.527887        1                 1            0.5802
118   0.526346        1                 1            0.5802
119   0.529035        1                 1            0.5802

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.538629        2                 2               1.0
85    0.533695        1                 1               1.0
86    0.520911        0                 0               1.0
87    0.522368        0                 0               1.0
88    0.537560        2                 2               1.0
89    0.544129        2                 2               1.0
90    0.533711        1                 1               1.0
91    0.520252        0                 0               1.0
92    0.529236        1                 1               1.0
93    0.521259        0                 0               1.0
94    0.544584        2                 2               1.0
95    0.516711        0                 0               1.0
96    0.528817        1                 1               1.0
97    0.524567        0                 0               1.0
98    0.533665        1                 1               1.0
99    0.522300        0                 0               1.0
100   0.540106        2                 2               1.0
101   0.521544        0                 0               1.0
102   0.524551        0                 0               1.0
103   0.538508        2                 2               1.0
104   0.531254        1                 1               1.0
105   0.538049        2                 2               1.0
106   0.528552        1                 1               1.0
107   0.541819        2                 2               1.0
108   0.529806        1                 1               1.0
109   0.532170        1                 1               1.0
110   0.555616        2                 2               1.0
111   0.521524        0                 0               1.0
112   0.518960        0                 0               1.0
113   0.533632        1                 1               1.0
114   0.521987        0                 0               1.0
115   0.537833        2                 2               1.0
116   0.526868        1                 1               1.0
117   0.527887        1                 1               1.0
118   0.526346        1                 1               1.0
119   0.529035        1                 1               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.538629        2                 2            0.9986
85    0.533695        1                 1            0.9978
86    0.520911        0                 0            0.9992
87    0.522368        0                 0            0.9990
88    0.537560        2                 2            0.9979
89    0.544129        2                 2            0.9987
90    0.533711        1                 1            0.9978
91    0.520252        0                 0            0.9992
92    0.529236        1                 1            0.9992
93    0.521259        0                 0            0.9992
94    0.544584        2                 2            0.9987
95    0.516711        0                 0            0.9989
96    0.528817        1                 1            0.9992
97    0.524567        0                 0            0.9977
98    0.533665        1                 1            0.9978
99    0.522300        0                 0            0.9990
100   0.540106        2                 2            0.9987
101   0.521544        0                 0            0.9991
102   0.524551        0                 0            0.9977
103   0.538508        2                 2            0.9986
104   0.531254        1                 1            0.9991
105   0.538049        2                 2            0.9983
106   0.528552        1                 1            0.9992
107   0.541819        2                 2            0.9988
108   0.529806        1                 1            0.9992
109   0.532170        1                 1            0.9988
110   0.555616        2                 2            0.9986
111   0.521524        0                 0            0.9991
112   0.518960        0                 0            0.9990
113   0.533632        1                 1            0.9978
114   0.521987        0                 0            0.9991
115   0.537833        2                 2            0.9983
116   0.526868        1                 1            0.9989
117   0.527887        1                 1            0.9992
118   0.526346        1                 1            0.9989
119   0.529035        1                 1            0.9992

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.538629        2                 2            0.6701
85    0.533695        1                 1            0.6444
86    0.520911        0                 0            0.6972
87    0.522368        0                 0            0.6953
88    0.537560        2                 2            0.6669
89    0.544129        2                 2            0.6721
90    0.533711        1                 1            0.6444
91    0.520252        0                 0            0.6972
92    0.529236        1                 1            0.7132
93    0.521259        0                 0            0.6972
94    0.544584        2                 2            0.6721
95    0.516711        0                 0            0.6972
96    0.528817        1                 1            0.7121
97    0.524567        0                 0            0.5459
98    0.533665        1                 1            0.6444
99    0.522300        0                 0            0.6953
100   0.540106        2                 2            0.6721
101   0.521544        0                 0            0.6972
102   0.524551        0                 0            0.5658
103   0.538508        2                 2            0.6701
104   0.531254        1                 1            0.7114
105   0.538049        2                 2            0.6683
106   0.528552        1                 1            0.7121
107   0.541819        2                 2            0.6721
108   0.529806        1                 1            0.7123
109   0.532170        1                 1            0.7050
110   0.555616        2                 2            0.6721
111   0.521524        0                 0            0.6972
112   0.518960        0                 0            0.6972
113   0.533632        1                 1            0.6444
114   0.521987        0                 0            0.6972
115   0.537833        2                 2            0.6683
116   0.526868        1                 1            0.7024
117   0.527887        1                 1            0.7109
118   0.526346        1                 1            0.6874
119   0.529035        1                 1            0.7121

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.538629        2                 2               1.0
85    0.533695        1                 1               1.0
86    0.520911        0                 0               1.0
87    0.522368        0                 0               1.0
88    0.537560        2                 2               1.0
89    0.544129        2                 2               1.0
90    0.533711        1                 1               1.0
91    0.520252        0                 0               1.0
92    0.529236        1                 1               1.0
93    0.521259        0                 0               1.0
94    0.544584        2                 2               1.0
95    0.516711        0                 0               1.0
96    0.528817        1                 1               1.0
97    0.524567        0                 0               1.0
98    0.533665        1                 1               1.0
99    0.522300        0                 0               1.0
100   0.540106        2                 2               1.0
101   0.521544        0                 0               1.0
102   0.524551        0                 0               1.0
103   0.538508        2                 2               1.0
104   0.531254        1                 1               1.0
105   0.538049        2                 2               1.0
106   0.528552        1                 1               1.0
107   0.541819        2                 2               1.0
108   0.529806        1                 1               1.0
109   0.532170        1                 1               1.0
110   0.555616        2                 2               1.0
111   0.521524        0                 0               1.0
112   0.518960        0                 0               1.0
113   0.533632        1                 1               1.0
114   0.521987        0                 0               1.0
115   0.537833        2                 2               1.0
116   0.526868        1                 1               1.0
117   0.527887        1                 1               1.0
118   0.526346        1                 1               1.0
119   0.529035        1                 1               1.0

In [129]:
T05_final_classification_model = finalize_model(T05_model_et)

T05_prediction = predict_model(T05_final_classification_model, data=T05_datas)

T05_y_class = pd.DataFrame(T05_class, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_prediction = pd.concat([T05_prediction, T05_y_class], axis = 1)
T05_prediction = T05_prediction.set_index('index')
T05_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# T01

In [130]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [131]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)

T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
index                                                                        
28              0.0    0.0  -0.25 -0.054348    0.0  1.011236   -1.0   -1.0   
33              0.0    0.0   1.25 -0.054348    0.0  1.101124   -1.0   -1.0   
39              0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
40              0.0    0.0   1.25 -0.054348    0.0  1.179775   -1.0   -1.0   
41              0.0    0.0  -0.75 -0.054348    0.0  1.179775   -1.0   -1.0   
...             ...    ...    ...       ...    ...       ...    ...    ...   
479             0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
501             0.0    1.0   1.25  1.293478    0.0  0.000000    0.0    0.0   
523             0.0    0.0  -0.25  1.423913    1.0  0.000000    0.0    0.0   
531             0.0    0.0   0.00  1.489130    0.0  0.000000    0.0    0.0   
585             0.0    0.0   0.75  0.630435    1.0  0.000000    0.0    0.0   

          X_256     X_257  ...    X_2857    X_2858    X_2859    X_2860  \
index                      ...                                           
28    -0.145455 -0.198381  ... -0.763158 -0.390876  0.000000 -0.053030   
33    -0.131818 -0.137652  ... -0.331579 -0.287500 -0.222798 -0.530303   
39    -0.072727 -0.097166  ... -0.163158 -1.014237 -0.621762  0.106061   
40     0.031818  0.000000  ... -0.489474 -0.542842 -1.191710  0.689394   
41     0.027273  0.000000  ... -0.931579 -1.034646 -1.492228 -0.022727   
...         ...       ...  ...       ...       ...       ...       ...   
479    0.068182  0.048583  ...  1.121053  0.285900  0.093264  0.045455   
501    0.295455  0.246964  ...  0.515789  0.550583 -0.134715  0.371212   
523    0.459091  0.421053  ...  0.200000  0.387683  0.424870  0.492424   
531    0.568182  0.481781  ...  0.000000  0.101173  0.279793  0.750000   
585   -0.172727 -0.234818  ...  0.773684  1.045072  1.056995  0.719697   

         X_2861    X_2862  X_2863    X_2864  X_2865  DAY_OF_WEEK  
index                                                             
28     0.321839  0.041096    -1.9 -1.452964    -5.0     0.666667  
33    -0.217241 -0.109589    -1.9 -1.500816    -5.0    -1.000000  
39     0.217816  0.404110    -1.8 -1.666123    -8.0    -0.666667  
40     0.663885  0.595890    -1.9 -1.604342    -5.0    -0.666667  
41    -0.040517  0.205479    -1.9 -1.524742    -8.5    -0.666667  
...         ...       ...     ...       ...     ...          ...  
479   -0.109329 -0.390411    -0.9 -0.482871    -5.0    -1.000000  
501    0.939778  1.041096     0.1  0.344334     1.0     0.000000  
523    0.902874  0.876712     0.1  0.264525     0.0     0.666667  
531    1.195135  0.910959     0.1  0.428577     2.0    -1.333333  
585    1.377586  1.150685     0.7  0.924415     4.5    -1.333333  

[129 rows x 736 columns]

In [132]:
from pycaret.regression import *
setup_rgs = setup(data = T01_data, target = T01_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [133]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [134]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [135]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
90            0.0    0.0   0.25 -0.054348    0.0  1.247191   -1.0   -1.0   
91            0.0    0.0  -0.25 -0.054348    0.0  0.146067    0.0   -1.0   
92            0.0    1.0   0.25 -0.054348    0.0  0.426966   -1.0   -1.0   
93            0.0    0.0  -0.25  1.597826    1.0  0.000000    0.0    0.0   
94            0.0    0.0  -0.50 -0.054348    0.0  1.876405   -1.0   -1.0   
95            0.0    0.0   1.00  1.478261    1.0  0.000000    0.0    0.0   
96            0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
97            0.0    0.0  -0.75 -0.054348    0.0  0.123596   -1.0   -1.0   
98            0.0    0.0   1.00  1.413043    0.0  0.000000    0.0    0.0   
99            0.0    0.0   1.25  0.663043    0.0  0.000000    0.0    0.0   
100           0.0    1.0  -0.50 -0.054348    0.0  1.426966   -1.0   -1.0   
101           0.0    1.0   1.50  0.326087    1.0  0.000000    0.0    0.0   
102           0.0    0.0  -0.25 -0.054348    0.0  0.955056    0.0   -1.0   
103           0.0    0.0   1.25 -0.054348    0.0  1.662921   -1.0   -1.0   
104           0.0    1.0   0.00 -0.054348    0.0  1.887640   -1.0   -1.0   
105           0.0    0.0   0.00  0.858696    0.0  0.000000    0.0    0.0   
106           0.0    0.0  -0.50  0.076087    1.0  0.000000    0.0    0.0   
107           0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
108           0.0    1.0  -0.25 -0.054348    0.0  1.831461   -1.0   -1.0   
109           0.0    0.0  -0.50  0.847826    1.0  0.000000    0.0    0.0   
110           0.0    0.0   1.25 -0.054348    0.0  0.247191   -1.0   -1.0   
111           0.0    0.0   1.25  0.000000    1.0  0.000000    0.0    0.0   
112           0.0    0.0   0.75  1.489130    0.0  0.000000    0.0    0.0   
113           0.0    1.0  -0.75 -0.054348    0.0  1.337079   -1.0   -1.0   
114           0.0    0.0   1.25  1.521739    0.0  0.000000    0.0    0.0   
115           0.0    0.0   0.25 -0.043478    1.0  0.000000    0.0    0.0   
116           0.0    0.0   0.25  1.445652    1.0  0.000000    0.0    0.0   
117           0.0    0.0   0.00 -0.054348    0.0  1.404494   -1.0   -1.0   
118           0.0    0.0   0.75  0.750000    1.0  0.000000    0.0    0.0   
119           0.0    1.0   0.25 -0.054348    0.0  1.449438   -1.0   -1.0   
120           0.0    1.0  -0.25 -0.054348    0.0  1.516854   -1.0   -1.0   
121           0.0   10.0   0.00 -0.054348    0.0  0.483146   -1.0   -1.0   
122           0.0    0.0   0.00 -0.054348    0.0  0.977528   -1.0   -1.0   
123           0.0    0.0   1.25  1.750000    0.0  0.000000    0.0    0.0   
124           0.0    1.0   0.75  0.869565    1.0  0.000000    0.0    0.0   
125           0.0    0.0  -0.50  0.945652    1.0  0.000000    0.0    0.0   
126           0.0    0.0  -0.50 -0.054348    0.0  1.078652   -1.0   -1.0   
127           0.0    1.0   1.25  1.793478    1.0  0.000000    0.0    0.0   
128           0.0    1.0  -0.75 -0.054348    0.0  1.280899   -1.0   -1.0   

        X_256     X_257  ...    X_2859    X_2860    X_2861    X_2862  X_2863  \
90   0.000000  0.012146  ... -0.031088  0.030303  0.324425  0.047945    -1.9   
91  -0.959091 -0.947368  ... -1.072539 -1.507576 -1.028376 -0.684932     0.1   
92  -0.281818 -0.356275  ...  0.072539  0.159091  0.323409 -0.623288    -0.9   
93   0.609091  0.570850  ... -0.155440 -0.204545 -0.174138 -0.397260    -1.9   
94   0.713636  0.688259  ... -0.652850 -2.007576 -1.426591 -0.616438     0.1   
95   0.581818  0.481781  ...  0.181347 -0.333333 -0.419540 -0.500000     0.1   
96  -0.072727 -0.097166  ... -0.621762  0.106061  0.217816  0.404110    -1.8   
97  -0.445455 -0.502024  ... -0.238342 -0.840909 -0.261710  0.356164     0.1   
98   0.640909  0.578947  ...  0.259067 -0.916667 -0.801293 -1.465753    -0.8   
99  -0.313636 -0.396761  ... -0.264249 -0.340909  0.038985 -0.383562    -0.9   
100  0.268182  0.246964  ...  0.735751  0.583333  1.154598  1.376712     0.1   
101 

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
90            0.0    0.0   0.25 -0.054348    0.0  1.247191   -1.0   -1.0   
91            0.0    0.0  -0.25 -0.054348    0.0  0.146067    0.0   -1.0   
92            0.0    1.0   0.25 -0.054348    0.0  0.426966   -1.0   -1.0   
93            0.0    0.0  -0.25  1.597826    1.0  0.000000    0.0    0.0   
94            0.0    0.0  -0.50 -0.054348    0.0  1.876405   -1.0   -1.0   
95            0.0    0.0   1.00  1.478261    1.0  0.000000    0.0    0.0   
96            0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
97            0.0    0.0  -0.75 -0.054348    0.0  0.123596   -1.0   -1.0   
98            0.0    0.0   1.00  1.413043    0.0  0.000000    0.0    0.0   
99            0.0    0.0   1.25  0.663043    0.0  0.000000    0.0    0.0   
100           0.0    1.0  -0.50 -0.054348    0.0  1.426966   -1.0   -1.0   
101           0.0    1.0   1.50  0.326087    1.0  0.000000    0.0    0.0   
102           0.0    0.0  -0.25 -0.054348    0.0  0.955056    0.0   -1.0   
103           0.0    0.0   1.25 -0.054348    0.0  1.662921   -1.0   -1.0   
104           0.0    1.0   0.00 -0.054348    0.0  1.887640   -1.0   -1.0   
105           0.0    0.0   0.00  0.858696    0.0  0.000000    0.0    0.0   
106           0.0    0.0  -0.50  0.076087    1.0  0.000000    0.0    0.0   
107           0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
108           0.0    1.0  -0.25 -0.054348    0.0  1.831461   -1.0   -1.0   
109           0.0    0.0  -0.50  0.847826    1.0  0.000000    0.0    0.0   
110           0.0    0.0   1.25 -0.054348    0.0  0.247191   -1.0   -1.0   
111           0.0    0.0   1.25  0.000000    1.0  0.000000    0.0    0.0   
112           0.0    0.0   0.75  1.489130    0.0  0.000000    0.0    0.0   
113           0.0    1.0  -0.75 -0.054348    0.0  1.337079   -1.0   -1.0   
114           0.0    0.0   1.25  1.521739    0.0  0.000000    0.0    0.0   
115           0.0    0.0   0.25 -0.043478    1.0  0.000000    0.0    0.0   
116           0.0    0.0   0.25  1.445652    1.0  0.000000    0.0    0.0   
117           0.0    0.0   0.00 -0.054348    0.0  1.404494   -1.0   -1.0   
118           0.0    0.0   0.75  0.750000    1.0  0.000000    0.0    0.0   
119           0.0    1.0   0.25 -0.054348    0.0  1.449438   -1.0   -1.0   
120           0.0    1.0  -0.25 -0.054348    0.0  1.516854   -1.0   -1.0   
121           0.0   10.0   0.00 -0.054348    0.0  0.483146   -1.0   -1.0   
122           0.0    0.0   0.00 -0.054348    0.0  0.977528   -1.0   -1.0   
123           0.0    0.0   1.25  1.750000    0.0  0.000000    0.0    0.0   
124           0.0    1.0   0.75  0.869565    1.0  0.000000    0.0    0.0   
125           0.0    0.0  -0.50  0.945652    1.0  0.000000    0.0    0.0   
126           0.0    0.0  -0.50 -0.054348    0.0  1.078652   -1.0   -1.0   
127           0.0    1.0   1.25  1.793478    1.0  0.000000    0.0    0.0   
128           0.0    1.0  -0.75 -0.054348    0.0  1.280899   -1.0   -1.0   

        X_256     X_257  ...    X_2859    X_2860    X_2861    X_2862  X_2863  \
90   0.000000  0.012146  ... -0.031088  0.030303  0.324425  0.047945    -1.9   
91  -0.959091 -0.947368  ... -1.072539 -1.507576 -1.028376 -0.684932     0.1   
92  -0.281818 -0.356275  ...  0.072539  0.159091  0.323409 -0.623288    -0.9   
93   0.609091  0.570850  ... -0.155440 -0.204545 -0.174138 -0.397260    -1.9   
94   0.713636  0.688259  ... -0.652850 -2.007576 -1.426591 -0.616438     0.1   
95   0.581818  0.481781  ...  0.181347 -0.333333 -0.419540 -0.500000     0.1   
96  -0.072727 -0.097166  ... -0.621762  0.106061  0.217816  0.404110    -1.8   
97  -0.445455 -0.502024  ... -0.238342 -0.840909 -0.261710  0.356164     0.1   
98   0.640909  0.578947  ...  0.259067 -0.916667 -0.801293 -1.465753    -0.8   
99  -0.313636 -0.396761  ... -0.264249 -0.340909  0.038985 -0.383562    -0.9   
100  0.268182  0.246964  ...  0.735751  0.583333  1.154598  1.376712     0.1   
101 

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
90            0.0    0.0   0.25 -0.054348    0.0  1.247191   -1.0   -1.0   
91            0.0    0.0  -0.25 -0.054348    0.0  0.146067    0.0   -1.0   
92            0.0    1.0   0.25 -0.054348    0.0  0.426966   -1.0   -1.0   
93            0.0    0.0  -0.25  1.597826    1.0  0.000000    0.0    0.0   
94            0.0    0.0  -0.50 -0.054348    0.0  1.876405   -1.0   -1.0   
95            0.0    0.0   1.00  1.478261    1.0  0.000000    0.0    0.0   
96            0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
97            0.0    0.0  -0.75 -0.054348    0.0  0.123596   -1.0   -1.0   
98            0.0    0.0   1.00  1.413043    0.0  0.000000    0.0    0.0   
99            0.0    0.0   1.25  0.663043    0.0  0.000000    0.0    0.0   
100           0.0    1.0  -0.50 -0.054348    0.0  1.426966   -1.0   -1.0   
101           0.0    1.0   1.50  0.326087    1.0  0.000000    0.0    0.0   
102           0.0    0.0  -0.25 -0.054348    0.0  0.955056    0.0   -1.0   
103           0.0    0.0   1.25 -0.054348    0.0  1.662921   -1.0   -1.0   
104           0.0    1.0   0.00 -0.054348    0.0  1.887640   -1.0   -1.0   
105           0.0    0.0   0.00  0.858696    0.0  0.000000    0.0    0.0   
106           0.0    0.0  -0.50  0.076087    1.0  0.000000    0.0    0.0   
107           0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
108           0.0    1.0  -0.25 -0.054348    0.0  1.831461   -1.0   -1.0   
109           0.0    0.0  -0.50  0.847826    1.0  0.000000    0.0    0.0   
110           0.0    0.0   1.25 -0.054348    0.0  0.247191   -1.0   -1.0   
111           0.0    0.0   1.25  0.000000    1.0  0.000000    0.0    0.0   
112           0.0    0.0   0.75  1.489130    0.0  0.000000    0.0    0.0   
113           0.0    1.0  -0.75 -0.054348    0.0  1.337079   -1.0   -1.0   
114           0.0    0.0   1.25  1.521739    0.0  0.000000    0.0    0.0   
115           0.0    0.0   0.25 -0.043478    1.0  0.000000    0.0    0.0   
116           0.0    0.0   0.25  1.445652    1.0  0.000000    0.0    0.0   
117           0.0    0.0   0.00 -0.054348    0.0  1.404494   -1.0   -1.0   
118           0.0    0.0   0.75  0.750000    1.0  0.000000    0.0    0.0   
119           0.0    1.0   0.25 -0.054348    0.0  1.449438   -1.0   -1.0   
120           0.0    1.0  -0.25 -0.054348    0.0  1.516854   -1.0   -1.0   
121           0.0   10.0   0.00 -0.054348    0.0  0.483146   -1.0   -1.0   
122           0.0    0.0   0.00 -0.054348    0.0  0.977528   -1.0   -1.0   
123           0.0    0.0   1.25  1.750000    0.0  0.000000    0.0    0.0   
124           0.0    1.0   0.75  0.869565    1.0  0.000000    0.0    0.0   
125           0.0    0.0  -0.50  0.945652    1.0  0.000000    0.0    0.0   
126           0.0    0.0  -0.50 -0.054348    0.0  1.078652   -1.0   -1.0   
127           0.0    1.0   1.25  1.793478    1.0  0.000000    0.0    0.0   
128           0.0    1.0  -0.75 -0.054348    0.0  1.280899   -1.0   -1.0   

        X_256     X_257  ...    X_2859    X_2860    X_2861    X_2862  X_2863  \
90   0.000000  0.012146  ... -0.031088  0.030303  0.324425  0.047945    -1.9   
91  -0.959091 -0.947368  ... -1.072539 -1.507576 -1.028376 -0.684932     0.1   
92  -0.281818 -0.356275  ...  0.072539  0.159091  0.323409 -0.623288    -0.9   
93   0.609091  0.570850  ... -0.155440 -0.204545 -0.174138 -0.397260    -1.9   
94   0.713636  0.688259  ... -0.652850 -2.007576 -1.426591 -0.616438     0.1   
95   0.581818  0.481781  ...  0.181347 -0.333333 -0.419540 -0.500000     0.1   
96  -0.072727 -0.097166  ... -0.621762  0.106061  0.217816  0.404110    -1.8   
97  -0.445455 -0.502024  ... -0.238342 -0.840909 -0.261710  0.356164     0.1   
98   0.640909  0.578947  ...  0.259067 -0.916667 -0.801293 -1.465753    -0.8   
99  -0.313636 -0.396761  ... -0.264249 -0.340909  0.038985 -0.383562    -0.9   
100  0.268182  0.246964  ...  0.735751  0.583333  1.154598  1.376712     0.1   
101 

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
90            0.0    0.0   0.25 -0.054348    0.0  1.247191   -1.0   -1.0   
91            0.0    0.0  -0.25 -0.054348    0.0  0.146067    0.0   -1.0   
92            0.0    1.0   0.25 -0.054348    0.0  0.426966   -1.0   -1.0   
93            0.0    0.0  -0.25  1.597826    1.0  0.000000    0.0    0.0   
94            0.0    0.0  -0.50 -0.054348    0.0  1.876405   -1.0   -1.0   
95            0.0    0.0   1.00  1.478261    1.0  0.000000    0.0    0.0   
96            0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
97            0.0    0.0  -0.75 -0.054348    0.0  0.123596   -1.0   -1.0   
98            0.0    0.0   1.00  1.413043    0.0  0.000000    0.0    0.0   
99            0.0    0.0   1.25  0.663043    0.0  0.000000    0.0    0.0   
100           0.0    1.0  -0.50 -0.054348    0.0  1.426966   -1.0   -1.0   
101           0.0    1.0   1.50  0.326087    1.0  0.000000    0.0    0.0   
102           0.0    0.0  -0.25 -0.054348    0.0  0.955056    0.0   -1.0   
103           0.0    0.0   1.25 -0.054348    0.0  1.662921   -1.0   -1.0   
104           0.0    1.0   0.00 -0.054348    0.0  1.887640   -1.0   -1.0   
105           0.0    0.0   0.00  0.858696    0.0  0.000000    0.0    0.0   
106           0.0    0.0  -0.50  0.076087    1.0  0.000000    0.0    0.0   
107           0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
108           0.0    1.0  -0.25 -0.054348    0.0  1.831461   -1.0   -1.0   
109           0.0    0.0  -0.50  0.847826    1.0  0.000000    0.0    0.0   
110           0.0    0.0   1.25 -0.054348    0.0  0.247191   -1.0   -1.0   
111           0.0    0.0   1.25  0.000000    1.0  0.000000    0.0    0.0   
112           0.0    0.0   0.75  1.489130    0.0  0.000000    0.0    0.0   
113           0.0    1.0  -0.75 -0.054348    0.0  1.337079   -1.0   -1.0   
114           0.0    0.0   1.25  1.521739    0.0  0.000000    0.0    0.0   
115           0.0    0.0   0.25 -0.043478    1.0  0.000000    0.0    0.0   
116           0.0    0.0   0.25  1.445652    1.0  0.000000    0.0    0.0   
117           0.0    0.0   0.00 -0.054348    0.0  1.404494   -1.0   -1.0   
118           0.0    0.0   0.75  0.750000    1.0  0.000000    0.0    0.0   
119           0.0    1.0   0.25 -0.054348    0.0  1.449438   -1.0   -1.0   
120           0.0    1.0  -0.25 -0.054348    0.0  1.516854   -1.0   -1.0   
121           0.0   10.0   0.00 -0.054348    0.0  0.483146   -1.0   -1.0   
122           0.0    0.0   0.00 -0.054348    0.0  0.977528   -1.0   -1.0   
123           0.0    0.0   1.25  1.750000    0.0  0.000000    0.0    0.0   
124           0.0    1.0   0.75  0.869565    1.0  0.000000    0.0    0.0   
125           0.0    0.0  -0.50  0.945652    1.0  0.000000    0.0    0.0   
126           0.0    0.0  -0.50 -0.054348    0.0  1.078652   -1.0   -1.0   
127           0.0    1.0   1.25  1.793478    1.0  0.000000    0.0    0.0   
128           0.0    1.0  -0.75 -0.054348    0.0  1.280899   -1.0   -1.0   

        X_256     X_257  ...    X_2859    X_2860    X_2861    X_2862  X_2863  \
90   0.000000  0.012146  ... -0.031088  0.030303  0.324425  0.047945    -1.9   
91  -0.959091 -0.947368  ... -1.072539 -1.507576 -1.028376 -0.684932     0.1   
92  -0.281818 -0.356275  ...  0.072539  0.159091  0.323409 -0.623288    -0.9   
93   0.609091  0.570850  ... -0.155440 -0.204545 -0.174138 -0.397260    -1.9   
94   0.713636  0.688259  ... -0.652850 -2.007576 -1.426591 -0.616438     0.1   
95   0.581818  0.481781  ...  0.181347 -0.333333 -0.419540 -0.500000     0.1   
96  -0.072727 -0.097166  ... -0.621762  0.106061  0.217816  0.404110    -1.8   
97  -0.445455 -0.502024  ... -0.238342 -0.840909 -0.261710  0.356164     0.1   
98   0.640909  0.578947  ...  0.259067 -0.916667 -0.801293 -1.465753    -0.8   
99  -0.313636 -0.396761  ... -0.264249 -0.340909  0.038985 -0.383562    -0.9   
100  0.268182  0.246964  ...  0.735751  0.583333  1.154598  1.376712     0.1   
101 

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
90            0.0    0.0   0.25 -0.054348    0.0  1.247191   -1.0   -1.0   
91            0.0    0.0  -0.25 -0.054348    0.0  0.146067    0.0   -1.0   
92            0.0    1.0   0.25 -0.054348    0.0  0.426966   -1.0   -1.0   
93            0.0    0.0  -0.25  1.597826    1.0  0.000000    0.0    0.0   
94            0.0    0.0  -0.50 -0.054348    0.0  1.876405   -1.0   -1.0   
95            0.0    0.0   1.00  1.478261    1.0  0.000000    0.0    0.0   
96            0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
97            0.0    0.0  -0.75 -0.054348    0.0  0.123596   -1.0   -1.0   
98            0.0    0.0   1.00  1.413043    0.0  0.000000    0.0    0.0   
99            0.0    0.0   1.25  0.663043    0.0  0.000000    0.0    0.0   
100           0.0    1.0  -0.50 -0.054348    0.0  1.426966   -1.0   -1.0   
101           0.0    1.0   1.50  0.326087    1.0  0.000000    0.0    0.0   
102           0.0    0.0  -0.25 -0.054348    0.0  0.955056    0.0   -1.0   
103           0.0    0.0   1.25 -0.054348    0.0  1.662921   -1.0   -1.0   
104           0.0    1.0   0.00 -0.054348    0.0  1.887640   -1.0   -1.0   
105           0.0    0.0   0.00  0.858696    0.0  0.000000    0.0    0.0   
106           0.0    0.0  -0.50  0.076087    1.0  0.000000    0.0    0.0   
107           0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
108           0.0    1.0  -0.25 -0.054348    0.0  1.831461   -1.0   -1.0   
109           0.0    0.0  -0.50  0.847826    1.0  0.000000    0.0    0.0   
110           0.0    0.0   1.25 -0.054348    0.0  0.247191   -1.0   -1.0   
111           0.0    0.0   1.25  0.000000    1.0  0.000000    0.0    0.0   
112           0.0    0.0   0.75  1.489130    0.0  0.000000    0.0    0.0   
113           0.0    1.0  -0.75 -0.054348    0.0  1.337079   -1.0   -1.0   
114           0.0    0.0   1.25  1.521739    0.0  0.000000    0.0    0.0   
115           0.0    0.0   0.25 -0.043478    1.0  0.000000    0.0    0.0   
116           0.0    0.0   0.25  1.445652    1.0  0.000000    0.0    0.0   
117           0.0    0.0   0.00 -0.054348    0.0  1.404494   -1.0   -1.0   
118           0.0    0.0   0.75  0.750000    1.0  0.000000    0.0    0.0   
119           0.0    1.0   0.25 -0.054348    0.0  1.449438   -1.0   -1.0   
120           0.0    1.0  -0.25 -0.054348    0.0  1.516854   -1.0   -1.0   
121           0.0   10.0   0.00 -0.054348    0.0  0.483146   -1.0   -1.0   
122           0.0    0.0   0.00 -0.054348    0.0  0.977528   -1.0   -1.0   
123           0.0    0.0   1.25  1.750000    0.0  0.000000    0.0    0.0   
124           0.0    1.0   0.75  0.869565    1.0  0.000000    0.0    0.0   
125           0.0    0.0  -0.50  0.945652    1.0  0.000000    0.0    0.0   
126           0.0    0.0  -0.50 -0.054348    0.0  1.078652   -1.0   -1.0   
127           0.0    1.0   1.25  1.793478    1.0  0.000000    0.0    0.0   
128           0.0    1.0  -0.75 -0.054348    0.0  1.280899   -1.0   -1.0   

        X_256     X_257  ...    X_2859    X_2860    X_2861    X_2862  X_2863  \
90   0.000000  0.012146  ... -0.031088  0.030303  0.324425  0.047945    -1.9   
91  -0.959091 -0.947368  ... -1.072539 -1.507576 -1.028376 -0.684932     0.1   
92  -0.281818 -0.356275  ...  0.072539  0.159091  0.323409 -0.623288    -0.9   
93   0.609091  0.570850  ... -0.155440 -0.204545 -0.174138 -0.397260    -1.9   
94   0.713636  0.688259  ... -0.652850 -2.007576 -1.426591 -0.616438     0.1   
95   0.581818  0.481781  ...  0.181347 -0.333333 -0.419540 -0.500000     0.1   
96  -0.072727 -0.097166  ... -0.621762  0.106061  0.217816  0.404110    -1.8   
97  -0.445455 -0.502024  ... -0.238342 -0.840909 -0.261710  0.356164     0.1   
98   0.640909  0.578947  ...  0.259067 -0.916667 -0.801293 -1.465753    -0.8   
99  -0.313636 -0.396761  ... -0.264249 -0.340909  0.038985 -0.383562    -0.9   
100  0.268182  0.246964  ...  0.735751  0.583333  1.154598  1.376712     0.1   
101 

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
90            0.0    0.0   0.25 -0.054348    0.0  1.247191   -1.0   -1.0   
91            0.0    0.0  -0.25 -0.054348    0.0  0.146067    0.0   -1.0   
92            0.0    1.0   0.25 -0.054348    0.0  0.426966   -1.0   -1.0   
93            0.0    0.0  -0.25  1.597826    1.0  0.000000    0.0    0.0   
94            0.0    0.0  -0.50 -0.054348    0.0  1.876405   -1.0   -1.0   
95            0.0    0.0   1.00  1.478261    1.0  0.000000    0.0    0.0   
96            0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
97            0.0    0.0  -0.75 -0.054348    0.0  0.123596   -1.0   -1.0   
98            0.0    0.0   1.00  1.413043    0.0  0.000000    0.0    0.0   
99            0.0    0.0   1.25  0.663043    0.0  0.000000    0.0    0.0   
100           0.0    1.0  -0.50 -0.054348    0.0  1.426966   -1.0   -1.0   
101           0.0    1.0   1.50  0.326087    1.0  0.000000    0.0    0.0   
102           0.0    0.0  -0.25 -0.054348    0.0  0.955056    0.0   -1.0   
103           0.0    0.0   1.25 -0.054348    0.0  1.662921   -1.0   -1.0   
104           0.0    1.0   0.00 -0.054348    0.0  1.887640   -1.0   -1.0   
105           0.0    0.0   0.00  0.858696    0.0  0.000000    0.0    0.0   
106           0.0    0.0  -0.50  0.076087    1.0  0.000000    0.0    0.0   
107           0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
108           0.0    1.0  -0.25 -0.054348    0.0  1.831461   -1.0   -1.0   
109           0.0    0.0  -0.50  0.847826    1.0  0.000000    0.0    0.0   
110           0.0    0.0   1.25 -0.054348    0.0  0.247191   -1.0   -1.0   
111           0.0    0.0   1.25  0.000000    1.0  0.000000    0.0    0.0   
112           0.0    0.0   0.75  1.489130    0.0  0.000000    0.0    0.0   
113           0.0    1.0  -0.75 -0.054348    0.0  1.337079   -1.0   -1.0   
114           0.0    0.0   1.25  1.521739    0.0  0.000000    0.0    0.0   
115           0.0    0.0   0.25 -0.043478    1.0  0.000000    0.0    0.0   
116           0.0    0.0   0.25  1.445652    1.0  0.000000    0.0    0.0   
117           0.0    0.0   0.00 -0.054348    0.0  1.404494   -1.0   -1.0   
118           0.0    0.0   0.75  0.750000    1.0  0.000000    0.0    0.0   
119           0.0    1.0   0.25 -0.054348    0.0  1.449438   -1.0   -1.0   
120           0.0    1.0  -0.25 -0.054348    0.0  1.516854   -1.0   -1.0   
121           0.0   10.0   0.00 -0.054348    0.0  0.483146   -1.0   -1.0   
122           0.0    0.0   0.00 -0.054348    0.0  0.977528   -1.0   -1.0   
123           0.0    0.0   1.25  1.750000    0.0  0.000000    0.0    0.0   
124           0.0    1.0   0.75  0.869565    1.0  0.000000    0.0    0.0   
125           0.0    0.0  -0.50  0.945652    1.0  0.000000    0.0    0.0   
126           0.0    0.0  -0.50 -0.054348    0.0  1.078652   -1.0   -1.0   
127           0.0    1.0   1.25  1.793478    1.0  0.000000    0.0    0.0   
128           0.0    1.0  -0.75 -0.054348    0.0  1.280899   -1.0   -1.0   

        X_256     X_257  ...    X_2859    X_2860    X_2861    X_2862  X_2863  \
90   0.000000  0.012146  ... -0.031088  0.030303  0.324425  0.047945    -1.9   
91  -0.959091 -0.947368  ... -1.072539 -1.507576 -1.028376 -0.684932     0.1   
92  -0.281818 -0.356275  ...  0.072539  0.159091  0.323409 -0.623288    -0.9   
93   0.609091  0.570850  ... -0.155440 -0.204545 -0.174138 -0.397260    -1.9   
94   0.713636  0.688259  ... -0.652850 -2.007576 -1.426591 -0.616438     0.1   
95   0.581818  0.481781  ...  0.181347 -0.333333 -0.419540 -0.500000     0.1   
96  -0.072727 -0.097166  ... -0.621762  0.106061  0.217816  0.404110    -1.8   
97  -0.445455 -0.502024  ... -0.238342 -0.840909 -0.261710  0.356164     0.1   
98   0.640909  0.578947  ...  0.259067 -0.916667 -0.801293 -1.465753    -0.8   
99  -0.313636 -0.396761  ... -0.264249 -0.340909  0.038985 -0.383562    -0.9   
100  0.268182  0.246964  ...  0.735751  0.583333  1.154598  1.376712     0.1   
101 

PRODUCT_CODE  X_246  X_247     X_248  X_250     X_251  X_253  X_254  \
90            0.0    0.0   0.25 -0.054348    0.0  1.247191   -1.0   -1.0   
91            0.0    0.0  -0.25 -0.054348    0.0  0.146067    0.0   -1.0   
92            0.0    1.0   0.25 -0.054348    0.0  0.426966   -1.0   -1.0   
93            0.0    0.0  -0.25  1.597826    1.0  0.000000    0.0    0.0   
94            0.0    0.0  -0.50 -0.054348    0.0  1.876405   -1.0   -1.0   
95            0.0    0.0   1.00  1.478261    1.0  0.000000    0.0    0.0   
96            0.0    0.0   1.25 -0.054348    0.0  1.146067    0.0   -1.0   
97            0.0    0.0  -0.75 -0.054348    0.0  0.123596   -1.0   -1.0   
98            0.0    0.0   1.00  1.413043    0.0  0.000000    0.0    0.0   
99            0.0    0.0   1.25  0.663043    0.0  0.000000    0.0    0.0   
100           0.0    1.0  -0.50 -0.054348    0.0  1.426966   -1.0   -1.0   
101           0.0    1.0   1.50  0.326087    1.0  0.000000    0.0    0.0   
102           0.0    0.0  -0.25 -0.054348    0.0  0.955056    0.0   -1.0   
103           0.0    0.0   1.25 -0.054348    0.0  1.662921   -1.0   -1.0   
104           0.0    1.0   0.00 -0.054348    0.0  1.887640   -1.0   -1.0   
105           0.0    0.0   0.00  0.858696    0.0  0.000000    0.0    0.0   
106           0.0    0.0  -0.50  0.076087    1.0  0.000000    0.0    0.0   
107           0.0    0.0   0.75  1.108696    0.0  0.000000    0.0    0.0   
108           0.0    1.0  -0.25 -0.054348    0.0  1.831461   -1.0   -1.0   
109           0.0    0.0  -0.50  0.847826    1.0  0.000000    0.0    0.0   
110           0.0    0.0   1.25 -0.054348    0.0  0.247191   -1.0   -1.0   
111           0.0    0.0   1.25  0.000000    1.0  0.000000    0.0    0.0   
112           0.0    0.0   0.75  1.489130    0.0  0.000000    0.0    0.0   
113           0.0    1.0  -0.75 -0.054348    0.0  1.337079   -1.0   -1.0   
114           0.0    0.0   1.25  1.521739    0.0  0.000000    0.0    0.0   
115           0.0    0.0   0.25 -0.043478    1.0  0.000000    0.0    0.0   
116           0.0    0.0   0.25  1.445652    1.0  0.000000    0.0    0.0   
117           0.0    0.0   0.00 -0.054348    0.0  1.404494   -1.0   -1.0   
118           0.0    0.0   0.75  0.750000    1.0  0.000000    0.0    0.0   
119           0.0    1.0   0.25 -0.054348    0.0  1.449438   -1.0   -1.0   
120           0.0    1.0  -0.25 -0.054348    0.0  1.516854   -1.0   -1.0   
121           0.0   10.0   0.00 -0.054348    0.0  0.483146   -1.0   -1.0   
122           0.0    0.0   0.00 -0.054348    0.0  0.977528   -1.0   -1.0   
123           0.0    0.0   1.25  1.750000    0.0  0.000000    0.0    0.0   
124           0.0    1.0   0.75  0.869565    1.0  0.000000    0.0    0.0   
125           0.0    0.0  -0.50  0.945652    1.0  0.000000    0.0    0.0   
126           0.0    0.0  -0.50 -0.054348    0.0  1.078652   -1.0   -1.0   
127           0.0    1.0   1.25  1.793478    1.0  0.000000    0.0    0.0   
128           0.0    1.0  -0.75 -0.054348    0.0  1.280899   -1.0   -1.0   

        X_256     X_257  ...    X_2859    X_2860    X_2861    X_2862  X_2863  \
90   0.000000  0.012146  ... -0.031088  0.030303  0.324425  0.047945    -1.9   
91  -0.959091 -0.947368  ... -1.072539 -1.507576 -1.028376 -0.684932     0.1   
92  -0.281818 -0.356275  ...  0.072539  0.159091  0.323409 -0.623288    -0.9   
93   0.609091  0.570850  ... -0.155440 -0.204545 -0.174138 -0.397260    -1.9   
94   0.713636  0.688259  ... -0.652850 -2.007576 -1.426591 -0.616438     0.1   
95   0.581818  0.481781  ...  0.181347 -0.333333 -0.419540 -0.500000     0.1   
96  -0.072727 -0.097166  ... -0.621762  0.106061  0.217816  0.404110    -1.8   
97  -0.445455 -0.502024  ... -0.238342 -0.840909 -0.261710  0.356164     0.1   
98   0.640909  0.578947  ...  0.259067 -0.916667 -0.801293 -1.465753    -0.8   
99  -0.313636 -0.396761  ... -0.264249 -0.340909  0.038985 -0.383562    -0.9   
100  0.268182  0.246964  ...  0.735751  0.583333  1.154598  1.376712     0.1   
101 

In [136]:
T01_final_regression_model = finalize_model(T01_model_gbr)

T01_prediction = predict_model(T01_final_regression_model, data=T01_data)

T01_datas = T01_prediction['prediction_label']
T01_datas = pd.DataFrame(T01_datas.values, columns = ['Y_Quality'])

T01y_idx= T01_class.index
T01y_idx = pd.DataFrame(T01y_idx, columns = ['index'])
T01_datas = pd.concat([T01y_idx, T01_datas], axis = 1)
T01_datas = T01_datas.set_index('index')
T01_datas

Y_Quality
index           
28      0.521619
33      0.526817
39      0.531680
40      0.530477
41      0.528963
...          ...
479     0.534920
501     0.533509
523     0.534384
531     0.560159
585     0.515535

[129 rows x 1 columns]

In [137]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T01_datas, 
                   target=T01_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [138]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [139]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [140]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]

for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531273        1                 1            0.9980
91    0.518225        0                 0            0.9906
92    0.524830        0                 0            0.9906
93    0.524351        0                 0            0.9906
94    0.527399        1                 1            0.9981
95    0.524782        0                 0            0.9906
96    0.530575        1                 1            0.9981
97    0.560160        2                 2            0.9853
98    0.535730        2                 2            0.9853
99    0.549337        2                 2            0.9853
100   0.528796        1                 1            0.9981
101   0.543937        2                 2            0.9853
102   0.547365        2                 2            0.9853
103   0.528825        1                 1            0.9981
104   0.547058        2                 2            0.9853
105   0.533005        1                 1            0.9969
106   0.532932        1                 1            0.9969
107   0.528631        1                 1            0.9981
108   0.531461        1                 1            0.9980
109   0.518539        0                 0            0.9906
110   0.528963        1                 1            0.9981
111   0.536648        2                 2            0.9853
112   0.531131        1                 1            0.9980
113   0.534615        1                 1            0.7161
114   0.535911        2                 2            0.9853
115   0.538372        2                 2            0.9853
116   0.530177        1                 1            0.9981
117   0.534520        1                 1            0.7161
118   0.528414        1                 1            0.9981
119   0.526975        1                 1            0.9934
120   0.525564        1                 1            0.6591
121   0.528062        1                 1            0.9981
122   0.531680        1                 1            0.9976
123   0.530060        1                 1            0.9981
124   0.527994        1                 1            0.9981
125   0.533231        1                 1            0.9961
126   0.536954        2                 2            0.9853
127   0.523328        0                 0            0.9906
128   0.538265        2                 2            0.9853

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531273        1                 1              1.00
91    0.518225        0                 0              1.00
92    0.524830        0                 0              0.97
93    0.524351        0                 0              0.98
94    0.527399        1                 1              1.00
95    0.524782        0                 0              0.97
96    0.530575        1                 1              1.00
97    0.560160        2                 2              1.00
98    0.535730        2                 2              1.00
99    0.549337        2                 2              1.00
100   0.528796        1                 1              1.00
101   0.543937        2                 2              1.00
102   0.547365        2                 2              1.00
103   0.528825        1                 1              1.00
104   0.547058        2                 2              1.00
105   0.533005        1                 1              1.00
106   0.532932        1                 1              1.00
107   0.528631        1                 1              1.00
108   0.531461        1                 1              1.00
109   0.518539        0                 0              1.00
110   0.528963        1                 1              1.00
111   0.536648        2                 2              1.00
112   0.531131        1                 1              1.00
113   0.534615        1                 1              0.69
114   0.535911        2                 2              1.00
115   0.538372        2                 2              1.00
116   0.530177        1                 1              1.00
117   0.534520        1                 1              0.93
118   0.528414        1                 1              1.00
119   0.526975        1                 1              1.00
120   0.525564        1                 0              0.84
121   0.528062        1                 1              1.00
122   0.531680        1                 1              1.00
123   0.530060        1                 1              1.00
124   0.527994        1                 1              1.00
125   0.533231        1                 1              1.00
126   0.536954        2                 2              1.00
127   0.523328        0                 0              1.00
128   0.538265        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531273        1                 1               1.0
91    0.518225        0                 0               1.0
92    0.524830        0                 0               1.0
93    0.524351        0                 0               1.0
94    0.527399        1                 1               1.0
95    0.524782        0                 0               1.0
96    0.530575        1                 1               1.0
97    0.560160        2                 2               1.0
98    0.535730        2                 2               1.0
99    0.549337        2                 2               1.0
100   0.528796        1                 1               1.0
101   0.543937        2                 2               1.0
102   0.547365        2                 2               1.0
103   0.528825        1                 1               1.0
104   0.547058        2                 2               1.0
105   0.533005        1                 1               1.0
106   0.532932        1                 1               1.0
107   0.528631        1                 1               1.0
108   0.531461        1                 1               1.0
109   0.518539        0                 0               1.0
110   0.528963        1                 1               1.0
111   0.536648        2                 2               1.0
112   0.531131        1                 1               1.0
113   0.534615        1                 1               1.0
114   0.535911        2                 2               1.0
115   0.538372        2                 2               1.0
116   0.530177        1                 1               1.0
117   0.534520        1                 1               1.0
118   0.528414        1                 1               1.0
119   0.526975        1                 1               1.0
120   0.525564        1                 0               1.0
121   0.528062        1                 1               1.0
122   0.531680        1                 1               1.0
123   0.530060        1                 1               1.0
124   0.527994        1                 1               1.0
125   0.533231        1                 1               1.0
126   0.536954        2                 2               1.0
127   0.523328        0                 0               1.0
128   0.538265        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531273        1                 1              1.00
91    0.518225        0                 0              1.00
92    0.524830        0                 0              1.00
93    0.524351        0                 0              1.00
94    0.527399        1                 1              1.00
95    0.524782        0                 0              1.00
96    0.530575        1                 1              1.00
97    0.560160        2                 2              1.00
98    0.535730        2                 2              1.00
99    0.549337        2                 2              1.00
100   0.528796        1                 1              1.00
101   0.543937        2                 2              1.00
102   0.547365        2                 2              1.00
103   0.528825        1                 1              1.00
104   0.547058        2                 2              1.00
105   0.533005        1                 1              1.00
106   0.532932        1                 1              1.00
107   0.528631        1                 1              1.00
108   0.531461        1                 1              1.00
109   0.518539        0                 0              1.00
110   0.528963        1                 1              1.00
111   0.536648        2                 2              1.00
112   0.531131        1                 1              1.00
113   0.534615        1                 1              0.51
114   0.535911        2                 2              1.00
115   0.538372        2                 2              1.00
116   0.530177        1                 1              1.00
117   0.534520        1                 1              0.72
118   0.528414        1                 1              1.00
119   0.526975        1                 1              1.00
120   0.525564        1                 0              0.57
121   0.528062        1                 1              1.00
122   0.531680        1                 1              1.00
123   0.530060        1                 1              1.00
124   0.527994        1                 1              1.00
125   0.533231        1                 1              1.00
126   0.536954        2                 2              1.00
127   0.523328        0                 0              1.00
128   0.538265        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531273        1                 1            0.9996
91    0.518225        0                 0            0.9975
92    0.524830        0                 0            0.9964
93    0.524351        0                 0            0.9972
94    0.527399        1                 1            0.9995
95    0.524782        0                 0            0.9964
96    0.530575        1                 1            0.9996
97    0.560160        2                 2            0.9984
98    0.535730        2                 2            0.9977
99    0.549337        2                 2            0.9990
100   0.528796        1                 1            0.9995
101   0.543937        2                 2            0.9992
102   0.547365        2                 2            0.9991
103   0.528825        1                 1            0.9995
104   0.547058        2                 2            0.9991
105   0.533005        1                 1            0.9995
106   0.532932        1                 1            0.9995
107   0.528631        1                 1            0.9995
108   0.531461        1                 1            0.9996
109   0.518539        0                 0            0.9975
110   0.528963        1                 1            0.9996
111   0.536648        2                 2            0.9990
112   0.531131        1                 1            0.9996
113   0.534615        1                 1            0.9937
114   0.535911        2                 2            0.9985
115   0.538372        2                 2            0.9992
116   0.530177        1                 1            0.9996
117   0.534520        1                 1            0.9937
118   0.528414        1                 1            0.9995
119   0.526975        1                 1            0.9994
120   0.525564        1                 0            0.9828
121   0.528062        1                 1            0.9995
122   0.531680        1                 1            0.9996
123   0.530060        1                 1            0.9996
124   0.527994        1                 1            0.9995
125   0.533231        1                 1            0.9995
126   0.536954        2                 2            0.9991
127   0.523328        0                 0            0.9974
128   0.538265        2                 2            0.9992

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531273        1                 1            0.9908
91    0.518225        0                 0            0.9676
92    0.524830        0                 0            0.9676
93    0.524351        0                 0            0.9676
94    0.527399        1                 1            0.9890
95    0.524782        0                 0            0.9676
96    0.530575        1                 1            0.9945
97    0.560160        2                 2            0.9849
98    0.535730        2                 2            0.9849
99    0.549337        2                 2            0.9849
100   0.528796        1                 1            0.9934
101   0.543937        2                 2            0.9849
102   0.547365        2                 2            0.9849
103   0.528825        1                 1            0.9934
104   0.547058        2                 2            0.9849
105   0.533005        1                 1            0.9895
106   0.532932        1                 1            0.9895
107   0.528631        1                 1            0.9934
108   0.531461        1                 1            0.9895
109   0.518539        0                 0            0.9676
110   0.528963        1                 1            0.9938
111   0.536648        2                 2            0.9849
112   0.531131        1                 1            0.9920
113   0.534615        1                 1            0.9895
114   0.535911        2                 2            0.9849
115   0.538372        2                 2            0.9849
116   0.530177        1                 1            0.9945
117   0.534520        1                 1            0.9895
118   0.528414        1                 1            0.9927
119   0.526975        1                 1            0.9844
120   0.525564        1                 0            0.9676
121   0.528062        1                 1            0.9903
122   0.531680        1                 1            0.9895
123   0.530060        1                 1            0.9945
124   0.527994        1                 1            0.9903
125   0.533231        1                 1            0.9895
126   0.536954        2                 2            0.9849
127   0.523328        0                 0            0.9676
128   0.538265        2                 2            0.9849

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.531273        1                 1            1.0000
91    0.518225        0                 0            0.9999
92    0.524830        0                 0            0.9999
93    0.524351        0                 0            0.9999
94    0.527399        1                 1            1.0000
95    0.524782        0                 0            0.9999
96    0.530575        1                 1            1.0000
97    0.560160        2                 2            0.5809
98    0.535730        2                 2            0.5809
99    0.549337        2                 2            0.5809
100   0.528796        1                 1            1.0000
101   0.543937        2                 2            0.5809
102   0.547365        2                 2            0.5809
103   0.528825        1                 1            1.0000
104   0.547058        2                 2            0.5809
105   0.533005        1                 1            1.0000
106   0.532932        1                 1            1.0000
107   0.528631        1                 1            1.0000
108   0.531461        1                 1            1.0000
109   0.518539        0                 0            0.9999
110   0.528963        1                 1            1.0000
111   0.536648        2                 2            0.5809
112   0.531131        1                 1            1.0000
113   0.534615        1                 1            1.0000
114   0.535911        2                 2            0.5809
115   0.538372        2                 2            0.5809
116   0.530177        1                 1            1.0000
117   0.534520        1                 1            1.0000
118   0.528414        1                 1            1.0000
119   0.526975        1                 1            1.0000
120   0.525564        1                 0            0.9999
121   0.528062        1                 1            1.0000
122   0.531680        1                 1            1.0000
123   0.530060        1                 1            1.0000
124   0.527994        1                 1            1.0000
125   0.533231        1                 1            1.0000
126   0.536954        2                 2            0.5809
127   0.523328        0                 0            0.9999
128   0.538265        2                 2            0.5809

In [141]:
T01_final_classification_model = finalize_model(T01_model_gbc)

T01_prediction = predict_model(T01_final_classification_model, data=T01_datas)

T01_prediction = pd.DataFrame(T01_prediction, columns = ['prediction_label'])

T01_y_class = pd.DataFrame(T01_class, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_prediction = pd.concat([T01_prediction, T01_y_class], axis = 1)
T01_prediction = T01_prediction.set_index('index')
T01_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# T10

In [142]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [143]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)

T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

PRODUCT_CODE   X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
index                                                                         
22              0.0   0.0  1.4  1.0  0.000000  0.0  0.0  0.653153  0.746725   
23              0.0   0.0  1.4  1.0  0.000000  0.0  0.0  0.662162  0.768559   
25              0.0   0.0  0.4  1.0  0.000000  0.0  0.0  0.788288  0.917031   
29              0.0   0.0  1.0  1.0  0.000000  0.0  0.0  0.747748  0.917031   
37              0.0   0.0  1.0  1.0  0.000000  0.0  0.0  0.792793  0.947598   
...             ...   ...  ...  ...       ...  ...  ...       ...       ...   
589             0.0  -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.549550 -1.519651   
590             0.0  -1.0 -1.2  0.0  0.833333  0.0  1.0 -1.527027 -1.506550   
591             0.0  -1.0 -1.6  0.0  0.833333  0.0  1.0 -1.531532 -1.506550   
593             0.0   0.0  0.0  0.0  0.833333  0.0  1.0 -1.396396 -1.358079   
597             1.0  19.0 -1.6  0.0  2.666667  0.0  1.0 -1.319820 -1.314410   

           X_13  ...      X_925      X_926  X_927  X_928      X_929  \
index            ...                                                  
22     0.714286  ...   0.586957   0.962572   0.66    0.0   0.386364   
23     0.723214  ... -34.804348 -45.815738 -29.52  -32.6 -38.275000   
25     0.852679  ...  -0.652174   0.022073   0.66    0.1   0.581818   
29     0.790179  ...   0.260870   0.606526   0.30    0.1   0.738636   
37     0.830357  ...   0.608696   0.544146   0.16    0.1   0.756818   
...         ...  ...        ...        ...    ...    ...        ...   
589   -1.504464  ...  -0.043478   0.092131   0.30    0.0   0.634091   
590   -1.419643  ...  -0.434783   0.241843   0.48    0.1   0.900000   
591   -1.473214  ...  -0.108696   0.231286   0.02    0.0   0.909091   
593   -1.366071  ...   0.239130   0.428023   0.28    0.1   0.895455   
597   -1.200893  ...   2.782609   3.893474   2.70    0.0  -0.172727   

           X_930  X_931       X_932  X_933  DAY_OF_WEEK  
index                                                    
22      0.111111    1.0    0.584058    0.0    -1.000000  
23    -32.111111 -136.0 -180.608692  -13.2    -1.000000  
25      1.000000    1.0    0.739130    0.0     0.666667  
29      1.000000    1.0    0.304348    0.0     0.666667  
37      1.000000    1.0    0.763768    0.1    -0.666667  
...          ...    ...         ...    ...          ...  
589     1.000000    1.0    1.130435    0.1    -1.000000  
590     1.111111    0.0   -0.086956    0.0    -0.666667  
591     1.000000    0.0    0.000000    0.0    -0.666667  
593     1.000000    0.0   -0.652174    0.0    -0.333333  
597     0.000000    0.0   -0.269565    0.0    -0.333333  

[349 rows x 576 columns]

In [144]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T10_data, target = T10_target, session_id = 4)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [145]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [146]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [147]:
T10_tuned_models = [T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]

for model in T10_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
244           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.000000  0.000000   
245           0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.373874 -0.336245   
246           0.0  0.0 -1.0  0.0  0.833333  0.0  1.0 -0.707207 -0.698690   
247           0.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.788288 -1.733624   
248           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.716216  0.724891   
..            ...  ...  ...  ...       ...  ...  ...       ...       ...   
344           0.0  0.0 -0.4  0.0  1.333333  0.0  1.0 -0.225225 -0.139738   
345           0.0  0.0 -1.2  0.0  2.000000  0.0  1.0 -2.954955 -2.799127   
346           0.0  0.0 -0.2  0.0  1.500000  0.0  1.0 -0.639640 -0.589520   
347           0.0 -1.0  1.4  0.0  0.000000  0.0  0.0  0.932432  1.043668   
348           0.0  0.0 -0.8  0.0  1.000000  0.0  1.0  0.364865  0.502183   

         X_13  ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
244  0.151786  ...   0.54    0.0  0.531818  0.111111    1.0  0.434783    0.1   
245 -0.241071  ...   0.12    0.1  0.661364  1.000000   -1.0 -0.608696    0.0   
246 -0.633929  ...  -0.52    0.0  0.181818  0.000000    0.0 -0.173913    0.0   
247 -1.723214  ...   0.86    0.1  0.972727  1.000000    1.0  0.449275    0.0   
248  0.843750  ...  -0.24   -0.9 -0.418182  0.111111    0.0  0.000000    0.0   
..        ...  ...    ...    ...       ...       ...    ...       ...    ...   
344 -0.272321  ...  -0.50    0.1  0.568182  0.888889    0.0 -0.521739    0.0   
345 -2.910714  ...  -1.32    0.1  0.184091  0.111111    0.0 -0.224638    0.0   
346 -0.580357  ...  -0.18   -0.1 -0.150000  0.111111   -1.0 -1.213043   -0.1   
347  0.964286  ...   0.86   -0.8 -0.288636  0.111111    0.0 -0.086956    0.0   
348  0.312500  ...   1.10    0.1  0.729545  1.000000    1.0 -0.359420    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
244     0.666667   0.525525          0.530737  
245    -0.666667   0.531676          0.530481  
246    -0.333333   0.529952          0.530713  
247    -1.000000   0.531376          0.530643  
248     0.666667   0.528473          0.530233  
..           ...        ...               ...  
344    -0.333333   0.526997          0.530566  
345     0.333333   0.537283          0.530011  
346     0.000000   0.527637          0.530556  
347     0.333333   0.525897          0.530678  
348     0.666667   0.532476          0.531007  

[105 rows x 578 columns]

PRODUCT_CODE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
244           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.000000  0.000000   
245           0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.373874 -0.336245   
246           0.0  0.0 -1.0  0.0  0.833333  0.0  1.0 -0.707207 -0.698690   
247           0.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.788288 -1.733624   
248           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.716216  0.724891   
..            ...  ...  ...  ...       ...  ...  ...       ...       ...   
344           0.0  0.0 -0.4  0.0  1.333333  0.0  1.0 -0.225225 -0.139738   
345           0.0  0.0 -1.2  0.0  2.000000  0.0  1.0 -2.954955 -2.799127   
346           0.0  0.0 -0.2  0.0  1.500000  0.0  1.0 -0.639640 -0.589520   
347           0.0 -1.0  1.4  0.0  0.000000  0.0  0.0  0.932432  1.043668   
348           0.0  0.0 -0.8  0.0  1.000000  0.0  1.0  0.364865  0.502183   

         X_13  ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
244  0.151786  ...   0.54    0.0  0.531818  0.111111    1.0  0.434783    0.1   
245 -0.241071  ...   0.12    0.1  0.661364  1.000000   -1.0 -0.608696    0.0   
246 -0.633929  ...  -0.52    0.0  0.181818  0.000000    0.0 -0.173913    0.0   
247 -1.723214  ...   0.86    0.1  0.972727  1.000000    1.0  0.449275    0.0   
248  0.843750  ...  -0.24   -0.9 -0.418182  0.111111    0.0  0.000000    0.0   
..        ...  ...    ...    ...       ...       ...    ...       ...    ...   
344 -0.272321  ...  -0.50    0.1  0.568182  0.888889    0.0 -0.521739    0.0   
345 -2.910714  ...  -1.32    0.1  0.184091  0.111111    0.0 -0.224638    0.0   
346 -0.580357  ...  -0.18   -0.1 -0.150000  0.111111   -1.0 -1.213043   -0.1   
347  0.964286  ...   0.86   -0.8 -0.288636  0.111111    0.0 -0.086956    0.0   
348  0.312500  ...   1.10    0.1  0.729545  1.000000    1.0 -0.359420    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
244     0.666667   0.525525          0.530220  
245    -0.666667   0.531676          0.530633  
246    -0.333333   0.529952          0.528516  
247    -1.000000   0.531376          0.532164  
248     0.666667   0.528473          0.530404  
..           ...        ...               ...  
344    -0.333333   0.526997          0.531342  
345     0.333333   0.537283          0.534180  
346     0.000000   0.527637          0.530382  
347     0.333333   0.525897          0.530041  
348     0.666667   0.532476          0.532024  

[105 rows x 578 columns]

PRODUCT_CODE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
244           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.000000  0.000000   
245           0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.373874 -0.336245   
246           0.0  0.0 -1.0  0.0  0.833333  0.0  1.0 -0.707207 -0.698690   
247           0.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.788288 -1.733624   
248           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.716216  0.724891   
..            ...  ...  ...  ...       ...  ...  ...       ...       ...   
344           0.0  0.0 -0.4  0.0  1.333333  0.0  1.0 -0.225225 -0.139738   
345           0.0  0.0 -1.2  0.0  2.000000  0.0  1.0 -2.954955 -2.799127   
346           0.0  0.0 -0.2  0.0  1.500000  0.0  1.0 -0.639640 -0.589520   
347           0.0 -1.0  1.4  0.0  0.000000  0.0  0.0  0.932432  1.043668   
348           0.0  0.0 -0.8  0.0  1.000000  0.0  1.0  0.364865  0.502183   

         X_13  ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
244  0.151786  ...   0.54    0.0  0.531818  0.111111    1.0  0.434783    0.1   
245 -0.241071  ...   0.12    0.1  0.661364  1.000000   -1.0 -0.608696    0.0   
246 -0.633929  ...  -0.52    0.0  0.181818  0.000000    0.0 -0.173913    0.0   
247 -1.723214  ...   0.86    0.1  0.972727  1.000000    1.0  0.449275    0.0   
248  0.843750  ...  -0.24   -0.9 -0.418182  0.111111    0.0  0.000000    0.0   
..        ...  ...    ...    ...       ...       ...    ...       ...    ...   
344 -0.272321  ...  -0.50    0.1  0.568182  0.888889    0.0 -0.521739    0.0   
345 -2.910714  ...  -1.32    0.1  0.184091  0.111111    0.0 -0.224638    0.0   
346 -0.580357  ...  -0.18   -0.1 -0.150000  0.111111   -1.0 -1.213043   -0.1   
347  0.964286  ...   0.86   -0.8 -0.288636  0.111111    0.0 -0.086956    0.0   
348  0.312500  ...   1.10    0.1  0.729545  1.000000    1.0 -0.359420    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
244     0.666667   0.525525          0.530122  
245    -0.666667   0.531676          0.530699  
246    -0.333333   0.529952          0.529576  
247    -1.000000   0.531376          0.531339  
248     0.666667   0.528473          0.529634  
..           ...        ...               ...  
344    -0.333333   0.526997          0.532518  
345     0.333333   0.537283          0.535644  
346     0.000000   0.527637          0.529588  
347     0.333333   0.525897          0.524181  
348     0.666667   0.532476          0.531690  

[105 rows x 578 columns]

PRODUCT_CODE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
244           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.000000  0.000000   
245           0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.373874 -0.336245   
246           0.0  0.0 -1.0  0.0  0.833333  0.0  1.0 -0.707207 -0.698690   
247           0.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.788288 -1.733624   
248           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.716216  0.724891   
..            ...  ...  ...  ...       ...  ...  ...       ...       ...   
344           0.0  0.0 -0.4  0.0  1.333333  0.0  1.0 -0.225225 -0.139738   
345           0.0  0.0 -1.2  0.0  2.000000  0.0  1.0 -2.954955 -2.799127   
346           0.0  0.0 -0.2  0.0  1.500000  0.0  1.0 -0.639640 -0.589520   
347           0.0 -1.0  1.4  0.0  0.000000  0.0  0.0  0.932432  1.043668   
348           0.0  0.0 -0.8  0.0  1.000000  0.0  1.0  0.364865  0.502183   

         X_13  ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
244  0.151786  ...   0.54    0.0  0.531818  0.111111    1.0  0.434783    0.1   
245 -0.241071  ...   0.12    0.1  0.661364  1.000000   -1.0 -0.608696    0.0   
246 -0.633929  ...  -0.52    0.0  0.181818  0.000000    0.0 -0.173913    0.0   
247 -1.723214  ...   0.86    0.1  0.972727  1.000000    1.0  0.449275    0.0   
248  0.843750  ...  -0.24   -0.9 -0.418182  0.111111    0.0  0.000000    0.0   
..        ...  ...    ...    ...       ...       ...    ...       ...    ...   
344 -0.272321  ...  -0.50    0.1  0.568182  0.888889    0.0 -0.521739    0.0   
345 -2.910714  ...  -1.32    0.1  0.184091  0.111111    0.0 -0.224638    0.0   
346 -0.580357  ...  -0.18   -0.1 -0.150000  0.111111   -1.0 -1.213043   -0.1   
347  0.964286  ...   0.86   -0.8 -0.288636  0.111111    0.0 -0.086956    0.0   
348  0.312500  ...   1.10    0.1  0.729545  1.000000    1.0 -0.359420    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
244     0.666667   0.525525          0.530088  
245    -0.666667   0.531676          0.531250  
246    -0.333333   0.529952          0.529735  
247    -1.000000   0.531376          0.530669  
248     0.666667   0.528473          0.529267  
..           ...        ...               ...  
344    -0.333333   0.526997          0.531852  
345     0.333333   0.537283          0.532817  
346     0.000000   0.527637          0.530294  
347     0.333333   0.525897          0.528761  
348     0.666667   0.532476          0.531192  

[105 rows x 578 columns]

PRODUCT_CODE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
244           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.000000  0.000000   
245           0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.373874 -0.336245   
246           0.0  0.0 -1.0  0.0  0.833333  0.0  1.0 -0.707207 -0.698690   
247           0.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.788288 -1.733624   
248           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.716216  0.724891   
..            ...  ...  ...  ...       ...  ...  ...       ...       ...   
344           0.0  0.0 -0.4  0.0  1.333333  0.0  1.0 -0.225225 -0.139738   
345           0.0  0.0 -1.2  0.0  2.000000  0.0  1.0 -2.954955 -2.799127   
346           0.0  0.0 -0.2  0.0  1.500000  0.0  1.0 -0.639640 -0.589520   
347           0.0 -1.0  1.4  0.0  0.000000  0.0  0.0  0.932432  1.043668   
348           0.0  0.0 -0.8  0.0  1.000000  0.0  1.0  0.364865  0.502183   

         X_13  ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
244  0.151786  ...   0.54    0.0  0.531818  0.111111    1.0  0.434783    0.1   
245 -0.241071  ...   0.12    0.1  0.661364  1.000000   -1.0 -0.608696    0.0   
246 -0.633929  ...  -0.52    0.0  0.181818  0.000000    0.0 -0.173913    0.0   
247 -1.723214  ...   0.86    0.1  0.972727  1.000000    1.0  0.449275    0.0   
248  0.843750  ...  -0.24   -0.9 -0.418182  0.111111    0.0  0.000000    0.0   
..        ...  ...    ...    ...       ...       ...    ...       ...    ...   
344 -0.272321  ...  -0.50    0.1  0.568182  0.888889    0.0 -0.521739    0.0   
345 -2.910714  ...  -1.32    0.1  0.184091  0.111111    0.0 -0.224638    0.0   
346 -0.580357  ...  -0.18   -0.1 -0.150000  0.111111   -1.0 -1.213043   -0.1   
347  0.964286  ...   0.86   -0.8 -0.288636  0.111111    0.0 -0.086956    0.0   
348  0.312500  ...   1.10    0.1  0.729545  1.000000    1.0 -0.359420    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
244     0.666667   0.525525          0.529878  
245    -0.666667   0.531676          0.531130  
246    -0.333333   0.529952          0.527844  
247    -1.000000   0.531376          0.531153  
248     0.666667   0.528473          0.527475  
..           ...        ...               ...  
344    -0.333333   0.526997          0.532280  
345     0.333333   0.537283          0.535911  
346     0.000000   0.527637          0.529630  
347     0.333333   0.525897          0.527339  
348     0.666667   0.532476          0.532274  

[105 rows x 578 columns]

PRODUCT_CODE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
244           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.000000  0.000000   
245           0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.373874 -0.336245   
246           0.0  0.0 -1.0  0.0  0.833333  0.0  1.0 -0.707207 -0.698690   
247           0.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.788288 -1.733624   
248           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.716216  0.724891   
..            ...  ...  ...  ...       ...  ...  ...       ...       ...   
344           0.0  0.0 -0.4  0.0  1.333333  0.0  1.0 -0.225225 -0.139738   
345           0.0  0.0 -1.2  0.0  2.000000  0.0  1.0 -2.954955 -2.799127   
346           0.0  0.0 -0.2  0.0  1.500000  0.0  1.0 -0.639640 -0.589520   
347           0.0 -1.0  1.4  0.0  0.000000  0.0  0.0  0.932432  1.043668   
348           0.0  0.0 -0.8  0.0  1.000000  0.0  1.0  0.364865  0.502183   

         X_13  ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
244  0.151786  ...   0.54    0.0  0.531818  0.111111    1.0  0.434783    0.1   
245 -0.241071  ...   0.12    0.1  0.661364  1.000000   -1.0 -0.608696    0.0   
246 -0.633929  ...  -0.52    0.0  0.181818  0.000000    0.0 -0.173913    0.0   
247 -1.723214  ...   0.86    0.1  0.972727  1.000000    1.0  0.449275    0.0   
248  0.843750  ...  -0.24   -0.9 -0.418182  0.111111    0.0  0.000000    0.0   
..        ...  ...    ...    ...       ...       ...    ...       ...    ...   
344 -0.272321  ...  -0.50    0.1  0.568182  0.888889    0.0 -0.521739    0.0   
345 -2.910714  ...  -1.32    0.1  0.184091  0.111111    0.0 -0.224638    0.0   
346 -0.580357  ...  -0.18   -0.1 -0.150000  0.111111   -1.0 -1.213043   -0.1   
347  0.964286  ...   0.86   -0.8 -0.288636  0.111111    0.0 -0.086956    0.0   
348  0.312500  ...   1.10    0.1  0.729545  1.000000    1.0 -0.359420    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
244     0.666667   0.525525          0.530344  
245    -0.666667   0.531676          0.530418  
246    -0.333333   0.529952          0.530344  
247    -1.000000   0.531376          0.530502  
248     0.666667   0.528473          0.530294  
..           ...        ...               ...  
344    -0.333333   0.526997          0.530383  
345     0.333333   0.537283          0.530599  
346     0.000000   0.527637          0.530424  
347     0.333333   0.525897          0.530502  
348     0.666667   0.532476          0.530477  

[105 rows x 578 columns]

PRODUCT_CODE  X_1  X_2  X_5       X_7  X_8  X_9      X_11      X_12  \
244           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.000000  0.000000   
245           0.0  0.0  0.4  1.0  0.000000  0.0  0.0 -0.373874 -0.336245   
246           0.0  0.0 -1.0  0.0  0.833333  0.0  1.0 -0.707207 -0.698690   
247           0.0 -1.0 -0.2  0.0  0.833333  0.0  1.0 -1.788288 -1.733624   
248           0.0  0.0 -0.4  1.0  0.000000  0.0  0.0  0.716216  0.724891   
..            ...  ...  ...  ...       ...  ...  ...       ...       ...   
344           0.0  0.0 -0.4  0.0  1.333333  0.0  1.0 -0.225225 -0.139738   
345           0.0  0.0 -1.2  0.0  2.000000  0.0  1.0 -2.954955 -2.799127   
346           0.0  0.0 -0.2  0.0  1.500000  0.0  1.0 -0.639640 -0.589520   
347           0.0 -1.0  1.4  0.0  0.000000  0.0  0.0  0.932432  1.043668   
348           0.0  0.0 -0.8  0.0  1.000000  0.0  1.0  0.364865  0.502183   

         X_13  ...  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
244  0.151786  ...   0.54    0.0  0.531818  0.111111    1.0  0.434783    0.1   
245 -0.241071  ...   0.12    0.1  0.661364  1.000000   -1.0 -0.608696    0.0   
246 -0.633929  ...  -0.52    0.0  0.181818  0.000000    0.0 -0.173913    0.0   
247 -1.723214  ...   0.86    0.1  0.972727  1.000000    1.0  0.449275    0.0   
248  0.843750  ...  -0.24   -0.9 -0.418182  0.111111    0.0  0.000000    0.0   
..        ...  ...    ...    ...       ...       ...    ...       ...    ...   
344 -0.272321  ...  -0.50    0.1  0.568182  0.888889    0.0 -0.521739    0.0   
345 -2.910714  ...  -1.32    0.1  0.184091  0.111111    0.0 -0.224638    0.0   
346 -0.580357  ...  -0.18   -0.1 -0.150000  0.111111   -1.0 -1.213043   -0.1   
347  0.964286  ...   0.86   -0.8 -0.288636  0.111111    0.0 -0.086956    0.0   
348  0.312500  ...   1.10    0.1  0.729545  1.000000    1.0 -0.359420    0.0   

     DAY_OF_WEEK  Y_Quality  prediction_label  
244     0.666667   0.525525          0.530323  
245    -0.666667   0.531676          0.530323  
246    -0.333333   0.529952          0.530323  
247    -1.000000   0.531376          0.530323  
248     0.666667   0.528473          0.530323  
..           ...        ...               ...  
344    -0.333333   0.526997          0.530323  
345     0.333333   0.537283          0.530323  
346     0.000000   0.527637          0.530323  
347     0.333333   0.525897          0.530323  
348     0.666667   0.532476          0.530323  

[105 rows x 578 columns]

In [148]:
T10_final_regression_model = finalize_model(T10_model_et)

T10_prediction = predict_model(T10_final_regression_model, data=T10_data)

T10_datas = T10_prediction['prediction_label']
T10_datas = pd.DataFrame(T10_datas.values, columns = ['Y_Quality'])

T10y_idx= T10_class.index
T10y_idx = pd.DataFrame(T10y_idx, columns = ['index'])
T10_datas = pd.concat([T10y_idx, T10_datas], axis = 1)
T10_datas = T10_datas.set_index('index')

In [149]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T10_datas, 
                   target=T10_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [150]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [151]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [152]:
T10_tuned_models = [T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]

for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1            0.9999
245   0.526546        1                 1            0.9998
246   0.529225        1                 1            0.9999
247   0.532268        1                 1            0.9999
248   0.519090        0                 0            0.9986
..         ...      ...               ...               ...
344   0.534122        1                 1            0.9996
345   0.529948        1                 1            0.9999
346   0.524862        0                 0            0.9931
347   0.529017        1                 1            0.9999
348   0.533338        1                 1            0.9999

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1            0.9990
245   0.526546        1                 1            0.9926
246   0.529225        1                 1            0.9991
247   0.532268        1                 1            0.9991
248   0.519090        0                 0            0.9813
..         ...      ...               ...               ...
344   0.534122        1                 1            0.9904
345   0.529948        1                 1            0.9991
346   0.524862        0                 0            0.9813
347   0.529017        1                 1            0.9991
348   0.533338        1                 1            0.9940

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1               1.0
245   0.526546        1                 1               1.0
246   0.529225        1                 1               1.0
247   0.532268        1                 1               1.0
248   0.519090        0                 0               1.0
..         ...      ...               ...               ...
344   0.534122        1                 1               1.0
345   0.529948        1                 1               1.0
346   0.524862        0                 0               1.0
347   0.529017        1                 1               1.0
348   0.533338        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527714        1                 1            0.9997
245   0.526546        1                 1            0.9996
246   0.529225        1                 1            0.9997
247   0.532268        1                 1            0.9997
248   0.519090        0                 0            0.9997
..         ...      ...               ...               ...
344   0.534122        1                 1            0.9996
345   0.529948        1                 1            0.9997
346   0.524862        0                 0            0.6548
347   0.529017        1                 1            0.9997
348   0.533338        1                 1            0.9997

[105 rows x 4 columns]

In [153]:
T10_final_classification_model = finalize_model(T10_model_gbc)

T10_prediction = predict_model(T10_final_classification_model, data=T10_datas)

T10_y_class = pd.DataFrame(T10_class, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_prediction = pd.concat([T10_prediction, T10_y_class], axis = 1)
T10_prediction = T10_prediction.set_index('index')
T10_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# Test

In [154]:
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [155]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

test_data = test_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE', 'HOUR'], axis = 1)

In [156]:
test_data.drop(colls, inplace = True, axis = 1)

In [157]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  \
0       NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1       NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2       NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     467.0  444.192308   423.0     NaN     NaN     NaN     NaN     NaN   
4     465.0  443.211539   423.0     NaN     NaN     NaN     NaN     NaN   
..      ...         ...     ...     ...     ...     ...     ...     ...   
305     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309     NaN         NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2871  DAY_OF_WEEK  
0       NaN            5  
1       NaN            5  
2       NaN            5  
3       NaN            5  
4       NaN            5  
..      ...          ...  
305     NaN            6  
306     NaN            6  
307     NaN            6  
308     NaN            6  
309     NaN            6  

[310 rows x 2796 columns]

In [158]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']

TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [159]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)

In [160]:
TT05 = pd.concat([TT050304, TT050307])
TT01 = pd.concat([TT010305, TT010306])
TT10 = pd.concat([TT100304, TT100306])

TT05.drop(T5drop, inplace = True, axis = 1)
TT01.drop(T0drop, inplace = True, axis = 1)
TT10.drop(T1drop, inplace = True, axis = 1)

#TT05 = TT05.fillna(T05.mean())
#TT01 = TT01.fillna(T01.mean())
#TT10 = TT10.fillna(T10.mean())

TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)

In [161]:
TT05.drop(T05_cols, inplace = True, axis = 1)
TT01.drop(T01_cols, inplace = True, axis = 1)
TT10.drop(T10_cols, inplace = True, axis = 1)

In [162]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])

TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)

TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

In [163]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])

TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)

TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')

In [164]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])

TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)

TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')

In [165]:
from pycaret.regression import *
TT05_prediction = predict_model(T05_final_regression_model, data=TT05)
TT01_prediction = predict_model(T01_final_regression_model, data=TT01)
TT10_prediction = predict_model(T10_final_regression_model, data=TT10)

TT05_prediction = pd.DataFrame(TT05_prediction, columns = ['prediction_label'])
TT01_prediction = pd.DataFrame(TT01_prediction, columns = ['prediction_label'])
TT10_prediction = pd.DataFrame(TT10_prediction, columns = ['prediction_label'])

In [166]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT01_y_class = pd.DataFrame(TT01, columns = ['PRODUCT_CODE'])
TT01_idx = TT01_y_class.index
TT01_y_class = TT01_y_class.reset_index()
TT01_prediction = pd.concat([TT01_prediction, TT01_y_class], axis = 1)
TT01_prediction = TT01_prediction.set_index('index')
TT01_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

TT10_y_class = pd.DataFrame(TT10, columns = ['PRODUCT_CODE'])
TT10_idx = TT10_y_class.index
TT10_y_class = TT10_y_class.reset_index()
TT10_prediction = pd.concat([TT10_prediction, TT10_y_class], axis = 1)
TT10_prediction = TT10_prediction.set_index('index')
TT10_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [167]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas = pd.DataFrame(TT05_datas.values, columns = ['Y_Quality'])

TT05y_idx= TT05_prediction.index
TT05y_idx = pd.DataFrame(TT05y_idx, columns = ['index'])
TT05_datas = pd.concat([TT05y_idx, TT05_datas], axis = 1)
TT05_datas = TT05_datas.set_index('index')

TT01_datas = TT01_prediction['prediction_label']
TT01_datas = pd.DataFrame(TT01_datas.values, columns = ['Y_Quality'])

TT01y_idx= TT01_prediction.index
TT01y_idx = pd.DataFrame(TT01y_idx, columns = ['index'])
TT01_datas = pd.concat([TT01y_idx, TT01_datas], axis = 1)
TT01_datas = TT01_datas.set_index('index')

TT10_datas = TT10_prediction['prediction_label']
TT10_datas = pd.DataFrame(TT10_datas.values, columns = ['Y_Quality'])

TT10y_idx= TT10_prediction.index
TT10y_idx = pd.DataFrame(TT10y_idx, columns = ['index'])
TT10_datas = pd.concat([TT10y_idx, TT10_datas], axis = 1)
TT10_datas = TT10_datas.set_index('index')

In [168]:
from pycaret.classification import *

TT05_predictions = predict_model(T05_final_classification_model, data=TT05_datas)
TT01_predictions = predict_model(T01_final_classification_model, data=TT01_datas)
TT10_predictions = predict_model(T10_final_classification_model, data=TT10_datas)

TT05_predictions = pd.DataFrame(TT05_predictions, columns = ['prediction_label'])
TT01_predictions = pd.DataFrame(TT01_predictions, columns = ['prediction_label'])
TT10_predictions = pd.DataFrame(TT10_predictions, columns = ['prediction_label'])

In [169]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')

TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')

TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')

In [170]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

prediction_label
index                  
7                     0
8                     0
14                    0
35                    0
41                    0
...                 ...
301                   1
305                   1
307                   1
308                   1
309                   1

[310 rows x 1 columns]

In [171]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      0
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int32

In [172]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line3_dropotherstd0_robust_regpyc_classpyc_fill0_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        0
4   TEST_004        1

In [173]:
final_test['prediction_label'].value_counts()

1    249
0     33
2     28
Name: prediction_label, dtype: int64

In [174]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 0, 1, 1, 2, 0, 0, 1, 2, 2, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 2, 0, 1, 0, 0, 1,
       1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 0, 0,
       0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 0, 1,
       0, 1, 2, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1,
       1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 2, 2, 1, 1, 2, 1, 1, 1, 1, 0,
       0, 1, 2, 2, 1, 2, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1,